In [1]:
import os, jieba, json, re
import pandas as pd
import numpy as np

In [2]:
df = pd.read_csv('D:/pytel_data/outhet_excel_2/ikeamaster_ver7.csv',encoding='utf8')

In [3]:
df

index                                           Material  \
0        0                                                 []   
1        1  ['產品材質', '床底座/ 側板/ 背板/ 抽屜面板:', '\n密集板, 纖維板, 蜂巢...   
2        2                                                 []   
3        3  ['產品材質', '抽屜底板:', '\n纖維板, 壓克力漆\n', '床框側板:', '\...   
4        4  ['產品材質', '抽屜側板/ 抽屜背板:', '\n密集板, 美耐皿箔皮, 塑膠箔皮, A...   
..     ...                                                ...   
716   1312  ['產品材質', '桌腳/ 底框/ 薄金屬板:', '\n鋼質, 環氧/聚酯粉末塗料\n密集...   
717   1313                                                 []   
718   1314                                                 []   
719   1315                                                 []   
720   1316                                                 []   

                                   Product Information    Product number  \
0    [{'產品資訊': [' 可為賓客提供放鬆休息的空間；坐臥兩用床可當作躺椅、單人床或抬起、拉...  產品編號: 004.243.63   
1    [{'產品資訊': [' 白天是沙發，晚上是單人或雙人床；含兩個大抽屜，可收納棉被、枕頭和寢...  產品編號: 091.838.68   
2    [{'產品資訊': [' 可為賓客提供放鬆休息的空間；坐臥兩用床可當作躺椅、單人床或抬起、拉...  產品編號: 092.792.91   
3    [{'產品資訊': [' 白天是沙發，晚上是單人或雙人床；含兩個大抽屜，可收納棉被、枕頭和寢...  產品編號: 391.987.88   
4    [{'產品資訊': [' 白天是沙發，晚上是單人或雙人床；含兩個大抽屜，可收納棉被、枕頭和寢...  產品編號: 403.201.32   
..                                                 ...               ...   
716  [{'產品資訊': [' 實木貼皮表面，耐用、抗污，容易保持乾淨', ' 桌面深，可提供寬敞...  產品編號: 992.879.89   
717  [{'產品資訊': [' 實木貼皮表面，耐用、抗污，容易保持乾淨', ' 桌面深，可提供寬敞...  產品編號: 992.882.91   
718  [{'產品資訊': [' 可混搭桌面和桌腳；分開購買，打造適合空間的設計和尺寸', ' 蜂巢...  產品編號: 993.308.22   
719  [{'產品資訊': [' 可混搭桌面和桌腳；分開購買，打造適合空間的設計和尺寸', ' 含可...  產品編號: 993.313.03   
720  [{'產品資訊': [' 可混搭桌面和桌腳；分開購買，打造適合空間的設計和尺寸', ' 附可...  產品編號: 993.313.55   

                                              You know   colour  \
0    ['你要知道', '顧客利益', '既是沙發也是床', '如果想善用家裡的每一吋空間，不妨選...       白色   
1    ['你要知道', ' ', '附2張HUSVIKA彈簧床墊', '含床板條底座', '須搭配...       白色   
2    ['你要知道', '顧客利益', '既是沙發也是床', '如果想善用家裡的每一吋空間，不妨選...       白色   
3    ['你要知道', ' ', '寢具需另購', '須搭配兩張床墊(80x200公分)；當作單人...       白色   
4    ['你要知道', '顧客利益', '兼具休息和儲物功能', '居住空間不大或有時需要額外的床...       白色   
..                                                 ...      ...   
716  ['你要知道', ' ', '經測試，適合辦公室使用，並符合耐用度及穩定度的測試標準', '...      碳黑色   
717  ['你要知道', '顧客利益', '讓你方便工作', '只要簡單的按一下BEKANT電動式桌...    綠色/黑色   
718  ['你要知道', ' ', '附塑膠緩衝墊，放在桌子下方時可防止滑動', '設計師', 'I...      深灰色   
719  ['你要知道', ' ', '附桌腳與桌面的連接螺絲', '設計師', 'IKEA of S...   黑棕色/灰色   
720  ['你要知道', ' ', '附桌腳與桌面的連接螺絲', '設計師', 'IKEA of S...   黑棕色/灰色   

                 id                                             images  \
0    ikea004.243.63  ['https://www.ikea.com.tw/dairyfarm/tw/images/...   
1    ikea091.838.68  ['https://www.ikea.com.tw/dairyfarm/tw/images/...   
2    ikea092.792.91  ['https://www.ikea.com.tw/dairyfarm/tw/images/...   
3    ikea391.987.88  ['https://www.ikea.com.tw/dairyfarm/tw/images/...   
4    ikea403.201.32  ['https://www.ikea.com.tw/dairyfarm/tw/images/...   
..              ...                                                ...   
716  ikea992.879.89  ['https://www.ikea.com.tw/dairyfarm/tw/images/...   
717  ikea992.882.91  ['https://www.ikea.com.tw/dairyfarm/tw/images/...   
718  ikea993.308.22  ['https://www.ikea.com.tw/dairyfarm/tw/images/...   
719  ikea993.313.03  ['https://www.ikea.com.tw/dairyfarm/tw/images/...   
720  ikea993.313.55  ['https://www.ikea.com.tw/dairyfarm/tw/images/...   

        price                                               size  \
0     $ 6,990  [{'產品尺寸': ['長度:', '207 公分', '寬度:', '88 公分', '高...   
1    $ 16,880  [{'產品尺寸': ['長度:', '207 公分', '寬度:', '88 公分', '高...   
2    $ 10,970  [{'產品尺寸': ['長度:', '207 公分', '寬度:', '88 公分', '高...   
3    $ 14,788  [{'產品尺寸': ['抽屜高度(內側):', '21 公分', '長度:', '205 公...   
4    $ 12,900  [{'產品尺寸': ['長度:', '207 公分', '寬度:', '88 公分', '高...   
..        ...                                                ...   
716   $ 9,490  [{'產品尺寸': ['隔屏高度:', '55 公分', '長度:', '160 公分', ...   
717  $ 23,990  [{'產品尺寸': ['隔屏高度:', '120 公分', '長度:', '160 公分',...   
718  

### Product number

In [4]:
df_clearn_Product_number = df[['Product number']]

In [5]:
df_clearn_Product_number

Product number
0    產品編號: 004.243.63
1    產品編號: 091.838.68
2    產品編號: 092.792.91
3    產品編號: 391.987.88
4    產品編號: 403.201.32
..                ...
716  產品編號: 992.879.89
717  產品編號: 992.882.91
718  產品編號: 993.308.22
719  產品編號: 993.313.03
720  產品編號: 993.313.55

[721 rows x 1 columns]

In [6]:
df_clearn_Product_number_n = df_clearn_Product_number['Product number'].str.split('產品編號: ', expand=True) 

In [7]:
df_clearn_Product_number_n

0            1
0       004.243.63
1       091.838.68
2       092.792.91
3       391.987.88
4       403.201.32
..  ..         ...
716     992.879.89
717     992.882.91
718     993.308.22
719     993.313.03
720     993.313.55

[721 rows x 2 columns]

In [8]:
df_clearn_Product_number_n.columns = ['Index', 'Product_number_clearn']

In [9]:
df_clearn_Product_number_n[['Product_number_clearn']]

Product_number_clearn
0              004.243.63
1              091.838.68
2              092.792.91
3              391.987.88
4              403.201.32
..                    ...
716            992.879.89
717            992.882.91
718            993.308.22
719            993.313.03
720            993.313.55

[721 rows x 1 columns]

### price

In [10]:
df_clearn_price = df[['price']]

In [11]:
pd.set_option('display.max_rows', None)

In [12]:
df_clearn_price

price
0     $ 6,990
1    $ 16,880
2    $ 10,970
3    $ 14,788
4    $ 12,900
5    $ 12,900
6     $ 7,790
7     $ 7,990
8    $ 14,788
9    $ 19,898
10   $ 13,770
11   $ 13,900
12   $ 19,898
13   $ 19,898
14   $ 11,770
15   $ 13,988
16    $ 9,990
17   $ 11,490
18   $ 13,290
19    $ 8,990
20    $ 4,990
21   $ 12,700
22   $ 12,390
23   $ 10,790
24   $ 12,490
25    $ 6,490
26   $ 13,900
27    $ 9,490
28    $ 8,490
29   $ 13,290
30   $ 10,790
31   $ 12,990
32   $ 11,490
33   $ 10,190
34    $ 5,990
35    $ 4,990
36   $ 10,490
37    $ 9,790
38   $ 12,900
39   $ 11,900
40   $ 11,990
41   $ 14,490
42    $ 6,790
43   $ 10,190
44    $ 6,590
45   $ 13,690
46    $ 3,490
47    $ 9,490
48    $ 8,390
49    $ 6,990
50   $ 12,490
51    $ 9,990
52    $ 9,790
53    $ 3,490
54   $ 10,990
55   $ 14,490
56    $ 8,490
57   $ 18,050
58    $ 7,490
59    $ 8,790
60   $ 11,900
61    $ 9,590
62    $ 5,990
63    $ 9,390
64    $ 9,390
65   $ 15,990
66   $ 13,700
67    $ 5,790
68    $ 3,490
69    $ 7,490
70   $ 18,290
71    $ 6,290
72    $ 8,990
73   $ 10,490
74    $ 8,790
75    $ 7,290
76   $ 10,490
77    $ 8,990
78   $ 10,400
79    $ 9,990
80   $ 12,490
81   $ 11,990
82    $ 8,490
83    $ 7,690
84    $ 6,090
85    $ 6,090
86    $ 5,790
87   $ 21,250
88   $ 15,990
89   $ 12,900
90   $ 13,990
91   $ 11,490
92   $ 10,790
93   $ 12,900
94   $ 16,450
95   $ 15,880
96    $ 4,990
97    $ 7,990
98    $ 7,990
99   $ 10,990
100  $ 11,590
101   $ 9,990
102   $ 7,690
103   $ 5,290
104   $ 5,290
105  $ 12,790
106  $ 25,990
107  $ 11,490
108   $ 4,990
109   $ 5,990
110   $ 6,490
111   $ 8,790
112  $ 14,990
113  $ 11,900
114   $ 5,790
115  $ 10,390
116  $ 11,990
117  $ 12,790
118  $ 17,250
119  $ 13,900
120   $ 8,990
121   $ 7,590
122   $ 9,290
123  $ 13,490
124  $ 12,790
125   $ 6,790
126  $ 22,050
127   $ 7,490
128   $ 7,490
129   $ 6,490
130  $ 12,460
131   $ 3,990
132   $ 9,990
133   $ 7,590
134   $ 3,990
135   $ 7,990
136   $ 8,490
137   $ 4,290
138   $ 3,590
139   $ 9,390
140   $ 8,590
141   $ 8,990
142   $ 5,990
143   $ 1,990
144   $ 3,490
145   $ 8,090
146   $ 3,590
147   $ 6,590
148   $ 7,490
149   $ 7,390
150   $ 2,990
151   $ 4,390
152   $ 9,790
153   $ 3,790
154   $ 2,290
155   $ 5,590
156   $ 6,090
157   $ 6,990
158   $ 4,790
159   $ 5,490
160   $ 1,999
161   $ 1,490
162     $ 990
163     $ 399
164     $ 990
165   $ 1,999
166     $ 990
167   $ 2,599
168   $ 3,499
169   $ 1,290
170   $ 1,299
171   $ 2,790
172   $ 4,990
173   $ 8,990
174   $ 3,599
175   $ 1,695
176     $ 990
177   $ 1,195
178   $ 4,995
179   $ 1,990
180     $ 429
181     $ 429
182   $ 3,995
183   $ 4,495
184   $ 3,490
185   $ 3,990
186   $ 3,690
187   $ 3,990
188   $ 4,495
189   $ 3,690
190   $ 5,490
191     $ 299
192   $ 3,990
193   $ 2,495
194     $ 990
195     $ 895
196   $ 7,995
197   $ 3,995
198   $ 2,990
199   $ 1,795
200   $ 3,995
201   $ 1,990
202   $ 4,990
203   $ 4,495
204   $ 3,990
205   $ 1,990
206   $ 3,890
207   $ 3,890
208   $ 5,490
209   $ 1,290
210   $ 1,495
211   $ 7,995
212   $ 2,490
213   $ 1,795
214   $ 2,990
215     $ 995
216     $ 429
217   $ 1,995
218   $ 1,490
219   $ 3,990
220   $ 3,990
221   $ 3,490
222   $ 2,990
223   $ 2,990
224   $ 1,995
225     $ 995
226   $ 4,790
227   $ 1,290
228     $ 995
229   $ 2,995
230   $ 3,995
231   $ 7,995
232   $ 1,995
233   $ 3,690
234   $ 3,890
235     $ 895
236   $ 3,990
237   $ 1,990
238   $ 1,990
239   $ 3,995
240   $ 1,195
241   $ 1,795
242   $ 4,890
243   $ 4,790
244   $ 4,890
245   $ 3,490
246     $ 995
247   $ 6,990
248   $ 2,990
249   $ 8,995
250   $ 4,890
251   $ 3,890
252     $ 429
253     $ 895
254   $ 1,990
255     $ 299
256   $ 1,990
257     $ 499
258   $ 1,690
259   $ 1,290
260     $ 599
261   $ 1,990
262   $ 2,290
263   $ 1,290
264   $ 3,490
265     $ 829
266   $ 2,190
267   $ 4,290
268   $ 2,490
269     $ 729
270   $ 1,890
271   $ 2,190
272   $ 1,990
273     $ 875
274   $ 3,490
275   $ 4,790
276   $ 1,290
277   $ 1,390
278   $ 1,990
279   $ 1,690
280   $ 1,690
281   $ 2,490
282   $ 1,990
283   $ 2,290
284     $ 349
285 

In [13]:
df_clearn_price_n = df_clearn_price['price'].str.split('$', expand=True) 

In [14]:
df_clearn_price_n[1] = df_clearn_price_n[1].str.replace(',', '') 

In [15]:
df_clearn_price_n

0       1
0              6990
1             16880
2             10970
3             14788
4             12900
5             12900
6              7790
7              7990
8             14788
9             19898
10            13770
11            13900
12            19898
13            19898
14            11770
15            13988
16             9990
17            11490
18            13290
19             8990
20             4990
21            12700
22            12390
23            10790
24            12490
25             6490
26            13900
27             9490
28             8490
29            13290
30            10790
31            12990
32            11490
33            10190
34             5990
35             4990
36            10490
37             9790
38            12900
39            11900
40            11990
41            14490
42             6790
43            10190
44             6590
45            13690
46             3490
47             9490
48             8390
49             6990
50            12490
51             9990
52             9790
53             3490
54            10990
55            14490
56             8490
57            18050
58             7490
59             8790
60            11900
61             9590
62             5990
63             9390
64             9390
65            15990
66            13700
67             5790
68             3490
69             7490
70            18290
71             6290
72             8990
73            10490
74             8790
75             7290
76            10490
77             8990
78            10400
79             9990
80            12490
81            11990
82             8490
83             7690
84             6090
85             6090
86             5790
87            21250
88            15990
89            12900
90            13990
91            11490
92            10790
93            12900
94            16450
95            15880
96             4990
97             7990
98             7990
99            10990
100           11590
101            9990
102            7690
103            5290
104            5290
105           12790
106           25990
107           11490
108            4990
109            5990
110            6490
111            8790
112           14990
113           11900
114            5790
115           10390
116           11990
117           12790
118           17250
119           13900
120            8990
121            7590
122            9290
123           13490
124           12790
125            6790
126           22050
127            7490
128            7490
129            6490
130           12460
131            3990
132            9990
133            7590
134            3990
135            7990
136            8490
137            4290
138            3590
139            9390
140            8590
141            8990
142            5990
143            1990
144            3490
145            8090
146            3590
147            6590
148            7490
149            7390
150            2990
151            4390
152            9790
153            3790
154            2290
155            5590
156            6090
157            6990
158            4790
159            5490
160            1999
161            1490
162             990
163             399
164             990
165            1999
166             990
167            2599
168            3499
169            1290
170            1299
171            2790
172            4990
173            8990
174            3599
175            1695
176             990
177            1195
178            4995
179            1990
180             429
181             429
182            3995
183            4495
184            3490
185            3990
186            3690
187            3990
188            4495
189            3690
190            5490
191             299
192            3990
193            2495
194             990
195             895
196            7995
197            3995
198            2990
199       

In [16]:
#df_clearn_price_n.iloc[[655],1:2]

In [17]:
df_clearn_price_n[1][489] = 8490

In [18]:
df_clearn_price_n[1][493] = 1290

In [19]:
df_clearn_price_n[1][655] = 4490

In [20]:
df_clearn_price_n

0       1
0              6990
1             16880
2             10970
3             14788
4             12900
5             12900
6              7790
7              7990
8             14788
9             19898
10            13770
11            13900
12            19898
13            19898
14            11770
15            13988
16             9990
17            11490
18            13290
19             8990
20             4990
21            12700
22            12390
23            10790
24            12490
25             6490
26            13900
27             9490
28             8490
29            13290
30            10790
31            12990
32            11490
33            10190
34             5990
35             4990
36            10490
37             9790
38            12900
39            11900
40            11990
41            14490
42             6790
43            10190
44             6590
45            13690
46             3490
47             9490
48             8390
49             6990
50            12490
51             9990
52             9790
53             3490
54            10990
55            14490
56             8490
57            18050
58             7490
59             8790
60            11900
61             9590
62             5990
63             9390
64             9390
65            15990
66            13700
67             5790
68             3490
69             7490
70            18290
71             6290
72             8990
73            10490
74             8790
75             7290
76            10490
77             8990
78            10400
79             9990
80            12490
81            11990
82             8490
83             7690
84             6090
85             6090
86             5790
87            21250
88            15990
89            12900
90            13990
91            11490
92            10790
93            12900
94            16450
95            15880
96             4990
97             7990
98             7990
99            10990
100           11590
101            9990
102            7690
103            5290
104            5290
105           12790
106           25990
107           11490
108            4990
109            5990
110            6490
111            8790
112           14990
113           11900
114            5790
115           10390
116           11990
117           12790
118           17250
119           13900
120            8990
121            7590
122            9290
123           13490
124           12790
125            6790
126           22050
127            7490
128            7490
129            6490
130           12460
131            3990
132            9990
133            7590
134            3990
135            7990
136            8490
137            4290
138            3590
139            9390
140            8590
141            8990
142            5990
143            1990
144            3490
145            8090
146            3590
147            6590
148            7490
149            7390
150            2990
151            4390
152            9790
153            3790
154            2290
155            5590
156            6090
157            6990
158            4790
159            5490
160            1999
161            1490
162             990
163             399
164             990
165            1999
166             990
167            2599
168            3499
169            1290
170            1299
171            2790
172            4990
173            8990
174            3599
175            1695
176             990
177            1195
178            4995
179            1990
180             429
181             429
182            3995
183            4495
184            3490
185            3990
186            3690
187            3990
188            4495
189            3690
190            5490
191             299
192            3990
193            2495
194             990
195             895
196            7995
197            3995
198            2990
199       

In [21]:
df_clearn_price_n.columns = ['price','price_clearn']

In [22]:
df_clearn_price_n = pd.concat([df_clearn_Product_number_n['Product_number_clearn'],df_clearn_price['price'], df_clearn_price_n['price_clearn']], axis=1)

In [23]:
df_clearn_price_n

Product_number_clearn     price price_clearn
0              004.243.63   $ 6,990         6990
1              091.838.68  $ 16,880        16880
2              092.792.91  $ 10,970        10970
3              391.987.88  $ 14,788        14788
4              403.201.32  $ 12,900        12900
5              503.201.36  $ 12,900        12900
6              503.544.85   $ 7,790         7790
7              504.544.42   $ 7,990         7990
8              591.987.87  $ 14,788        14788
9              691.299.39  $ 19,898        19898
10             691.987.58  $ 13,770        13770
11             703.493.27  $ 13,900        13900
12             891.298.77  $ 19,898        19898
13             891.299.43  $ 19,898        19898
14             891.987.57  $ 11,770        11770
15             892.792.92  $ 13,988        13988
16             090.191.42   $ 9,990         9990
17             091.981.53  $ 11,490        11490
18             091.981.67  $ 13,290        13290
19             091.982.33   $ 8,990         8990
20             091.985.15   $ 4,990         4990
21             091.986.38  $ 12,700        12700
22             091.998.93  $ 12,390        12390
23             092.008.77  $ 10,790        10790
24             092.010.18  $ 12,490        12490
25             092.772.87   $ 6,490         6490
26             104.048.02  $ 13,900        13900
27             190.273.92   $ 9,490         9490
28             191.981.43   $ 8,490         8490
29             191.981.62  $ 13,290        13290
30             191.982.18  $ 10,790        10790
31             191.997.79  $ 12,990        12990
32             192.009.71  $ 11,490        11490
33             192.411.65  $ 10,190        10190
34             192.412.88   $ 5,990         5990
35             192.772.82   $ 4,990         4990
36             291.981.52  $ 10,490        10490
37             291.982.65   $ 9,790         9790
38             291.983.93  $ 12,900        12900
39             291.986.37  $ 11,900        11900
40             292.006.21  $ 11,990        11990
41             292.010.17  $ 14,490        14490
42             292.410.75   $ 6,790         6790
43             292.413.44  $ 10,190        10190
44             292.689.13   $ 6,590         6590
45             293.030.06  $ 13,690        13690
46             293.037.42   $ 3,490         3490
47             390.094.53   $ 9,490         9490
48             390.191.88   $ 8,390         8390
49             391.981.42   $ 6,990         6990
50             391.981.61  $ 12,490        12490
51             391.982.17   $ 9,990         9990
52             391.983.97   $ 9,790         9790
53             391.985.14   $ 3,490         3490
54             391.997.78  $ 10,990        10990
55             392.009.08  $ 14,490        14490
56             392.412.49   $ 8,490         8490
57             392.875.48  $ 18,050        18050
58             404.463.58   $ 7,490         7490
59             491.981.51   $ 8,790         8790
60             491.983.92  $ 11,900        11900
61             491.994.62   $ 9,590         9590
62             492.410.60   $ 5,990         5990
63             492.411.64   $ 9,390         9390
64             492.413.43   $ 9,390         9390
65             492.414.23  $ 15,990        15990
66             492.475.85  $ 13,700        13700
67             492.689.12   $ 5,790         5790
68             492.772.66   $ 3,490         3490
69             492.773.08   $ 7,490         7490
70             493.030.29  $ 18,290        18290
71             504.463.53   $ 6,290         6290
72             590.094.47   $ 8,990         8990
73             590.191.73  $ 10,490        10490
74             590.191.87   $ 8,790         8790
75             590.305.09   $ 7,290         7290
76             591.750.69  $ 10,490        10490
77             591.983.96   $ 8,990         8990
78             591.986.07  $ 10,400        10400
79             592.004.98   $ 9,990         9990
80             592.009.07  $ 12,490

In [24]:
#df_clearn_price_n == np.nan

In [25]:
#df_clearn_price_n.isnull().T.any()

In [26]:
#df_clearn_price_n.replace({'price_clearn':{489:8490}})

In [27]:
#df_clearn_price_n[['price_clearn']]

In [28]:
#df_clearn_price_n.replace({'price_clearn': {1: 100}})

In [29]:
#df_clearn_price_n['price_clearn'].replace('None')

### Color

In [30]:
df2 = pd.read_csv('D:/pytel_data/outhet_excel_2/ikeamaster_ver7_cleaning_color_1.csv',encoding='utf8')

In [31]:
df2

Unnamed: 0              id                            summary  \
0             0  ikea004.243.63                         坐臥兩用床框, 黑色   
1             1  ikea091.838.68        坐臥兩用床附2抽/2床墊, 白色/husvika 偏硬   
2             2  ikea092.792.91           坐臥兩用床附2床墊, 黑色/husvika 偏硬   
3             3  ikea391.987.88        坐臥兩用床附2抽/2床墊, 白色/malfors 偏硬   
4             4  ikea403.201.32                     坐臥兩用床框附2抽屜, 白色   
5             5  ikea503.201.36                    坐臥兩用床框附2抽屜, 黑棕色   
6             6  ikea503.544.85                     坐臥兩用床框附2抽屜, 白色   
7             7  ikea504.544.42                  坐臥兩用床, vansta 深藍色   
8             8  ikea591.987.87      坐臥兩用床附2抽/2床墊, 白色/malfors 軟硬適中   
9             9  ikea691.299.39     坐臥兩用床附2抽/2床墊, 黑棕色/malfors 軟硬適中   
10           10  ikea691.987.58        坐臥兩用床附2抽/2床墊, 白色/moshult 偏硬   
11           11  ikea703.493.27                      坐臥兩用床框/3抽, 白色   
12           12  ikea891.298.77        坐臥兩用床附2抽/2床墊, 白色/malfors 偏硬   
13           13  ikea891.299.43      坐臥兩用床附2抽/2床墊, 白色/malfors 軟硬適中   
14           14  ikea891.987.57        坐臥兩用床附2抽/2床墊, 白色/husvika 偏硬   
15           15  ikea892.792.92         坐臥兩用床附2床墊, 黑色/malfors 軟硬適中   
16           16  ikea090.191.42            雙人加大床框, 白色, 附lönset床底板條   
17           17  ikea091.981.53         雙人加大床框, 白色, 附lönset床底板條/抽屜   
18           18  ikea091.981.67                  雙人加大床框附抽屜/床頭板, 白色   
19           19  ikea091.982.33              雙人床框, 黑棕色, 附luröy床底板條   
20           20  ikea091.985.15               雙人床框, 松木, 附luröy床底板條   
21           21  ikea091.986.38              雙人床框, 白色, 附lönset床底板條   
22           22  ikea091.998.93      雙人床框, 白色, 附lönset床底板條/4件床底收納盒   
23           23  ikea092.008.77     雙人床框, 黑棕色, 附lönset床底板條/2件床底收納盒   
24           24  ikea092.010.18  雙人加大床框, 染白橡木, 附lönset床底板條/2件床底收納盒   
25           25  ikea092.772.87             雙人加大床框, 白色, 附luröy床底板條   
26           26  ikea104.048.02                  雙人掀床, 黑棕色, 附床板條底座   
27           27  ikea190.273.92           雙人加大床框, 染白橡木, 附luröy床底板條   
28           28  ikea191.981.43            雙人床框, 白色, 附luröy床底板條/抽屜   
29           29  ikea191.981.62       雙人床框, 白色, 附lönset床底板條/抽屜/床頭板   
30           30  ikea191.982.18              雙人床框, 樺木, 附lönset床底板條   
31           31  ikea191.997.79     雙人加大床框, 白色, 附luröy床底板條/4件床底收納盒   
32           32  ikea192.009.71   雙人加大床框, 染白橡木, 附luröy床底板條/2件床底收納盒   
33           33  ikea192.411.65       雙人床框, 黑棕色, 附lönset床底板條/4件收納盒   
34           34  ikea192.412.88               雙人床框, 白色, 附luröy床底板條   
35           35  ikea192.772.82               雙人床框, 白色, 附luröy床底板條   
36           36  ikea291.981.52          雙人加大床框, 白色, 附luröy床底板條/抽屜   
37           37  ikea291.982.65             雙人床框, 黑棕色, 附lönset床底板條   
38           38  ikea291.983.93           雙人加大床框, 黑棕色, 附lönset床底板條   
39           39  ikea291.986.37                       床框, 白色/luröy   
40           40  ikea292.006.21      雙人床框, 黑棕色, 附luröy床底板條/4件床底收納盒   
41           41  ikea292.010.17  雙人加大床框, 染白橡木, 附lönset床底板條/4件床底收納盒   
42           42  ikea292.410.75              雙人床框, 棕色, 附lönset床底板條   
43           43  ikea292.413.44        雙人床框, 白色, 附lönset床底板條/4件收納盒   
44           44  ikea292.689.13              雙人床框, 黑色, 附lönset床底板條   
45           45  ikea293.030.06            小型雙人床框, 白色, 附床板條底座/2件抽屜   
46           46  ikea293.037.42               雙人床框, 松木, 附luröy床底板條   
47           47  ikea390.094.53            雙人加大床框, 黑棕色, 附luröy床底板條   
48           48  ikea390.191.88              雙人床框, 白色, 附lönset床底板條   
49           49  ikea391.981.42                          床框附抽屜, 白色   
50           50  ikea391.981.61        雙人床框, 白色, 附luröy床底板條/抽屜/床頭板   
51           51  ikea391.982.17               雙人床框, 樺木, 附luröy床底板條   
52           52  ikea391.983.97              雙人床框, 白色, 附lönset床底板條   
53           53  ikea391.985.14                             床框, 松木   
54           54  ikea391.997.78     雙人加大床框, 白色, 附luröy床底板條/2件床底收納盒   
55           55  ikea392.009.08   雙人加大床框, 黑棕色, 附lönset床底板條/4件床底收納盒   
56           56

In [32]:
df_clearn_color_1 = df2[['color_3']]

In [33]:
df_clearn_color_1

color_3
0      None
1      None
2      None
3      None
4      None
5      None
6      None
7      None
8      None
9      None
10     None
11     None
12     None
13     None
14     None
15     None
16     None
17     None
18     None
19     None
20     None
21     None
22     None
23     None
24     None
25     None
26     None
27     None
28     None
29     None
30     None
31     None
32     None
33     None
34     None
35     None
36     None
37     None
38     None
39     None
40     None
41     None
42     None
43     None
44     None
45     None
46     None
47     None
48     None
49     None
50     None
51     None
52     None
53     None
54     None
55     None
56     None
57     None
58     None
59     None
60     None
61     None
62     None
63     None
64     None
65     None
66     None
67     None
68     None
69     None
70     None
71     None
72     None
73     None
74     None
75     None
76     None
77     None
78     None
79     None
80     None
81     None
82     None
83     None
84     None
85     None
86     None
87     None
88     None
89     None
90     None
91     None
92     None
93     None
94     None
95     None
96     None
97     None
98     None
99     None
100    None
101    None
102    None
103    None
104    None
105    None
106    None
107    None
108    None
109    None
110    None
111    None
112    None
113    None
114    None
115    None
116    None
117    None
118    None
119    None
120    None
121    None
122    None
123    None
124    None
125    None
126    None
127    None
128    None
129    None
130    None
131    None
132    None
133    None
134    None
135    None
136    None
137    None
138    None
139    None
140    None
141    None
142    None
143    None
144    None
145    None
146    None
147    None
148    None
149    None
150    None
151    None
152    None
153    None
154    None
155    None
156    None
157    None
158    None
159    None
160    None
161    None
162    None
163    None
164    None
165    None
166    None
167    None
168    None
169    None
170    None
171    None
172    None
173    None
174    None
175    None
176    None
177    None
178    None
179    None
180    None
181    None
182    None
183    None
184    None
185    None
186    None
187    None
188    None
189    None
190    None
191    None
192    None
193    None
194    None
195    None
196    None
197    None
198    None
199    None
200    None
201    None
202    None
203    None
204    None
205    None
206    None
207    None
208    None
209    None
210    None
211    None
212    None
213    None
214    None
215    None
216    None
217    None
218    None
219    None
220    None
221    None
222    None
223    None
224    None
225    None
226    None
227    None
228    None
229    None
230    None
231    None
232    None
233    None
234    None
235    None
236    None
237    None
238    None
239    None
240    None
241    None
242    None
243    None
244    None
245    None
246    None
247    None
248    None
249    None
250    None
251    None
252    None
253    None
254    None
255    None
256    None
257    None
258    None
259    None
260    None
261    None
262    None
263    None
264    None
265    None
266    None
267    None
268    None
269    None
270    None
271    None
272    None
273    None
274    None
275    None
276    None
277    None
278    None
279    None
280    None
281    None
282    None
283    None
284    None
285    None
286    None
287    None
288    None
289    None
290    None
291    None
292    None
293    None
294    None
295    None
296    None
297    None
298    None
299    None
300    None
301    None
302    None
303    None
304    None
305    None
306    None
307    None
308    None
309    None
310    None
311    None
312    None
313    None
314    None
315    None
316    None
317    None
318    None
319    None
320    None
321    None
322    None
323    None
324    None
325    None
326    None
327    None
328    None
329    None
330    None
331    None
332    N

In [34]:
df_clearn_color_1['color_3'] = df_clearn_color_1['color_3'].fillna(value='None')

<ipython-input-34-52a1e3a1a0cd>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clearn_color_1['color_3'] = df_clearn_color_1['color_3'].fillna(value='None')


In [35]:
df_clearn_color_remix = pd.concat([df2['color_1'], df2['color_2'], df_clearn_color_1], axis=1)

In [36]:
df_clearn_color_remix

color_1 color_2 color_3
0        黑色    None    None
1        白色    None    None
2        黑色    None    None
3        白色    None    None
4        白色    None    None
5       黑棕色    None    None
6        白色    None    None
7       深藍色    None    None
8        白色    None    None
9       黑棕色    None    None
10       白色    None    None
11       白色    None    None
12       白色    None    None
13       白色    None    None
14       白色    None    None
15       黑色    None    None
16       白色    None    None
17       白色    None    None
18       白色    None    None
19      黑棕色    None    None
20       松木    None    None
21       白色    None    None
22       白色    None    None
23      黑棕色    None    None
24     染白橡木    None    None
25       白色    None    None
26      黑棕色    None    None
27     染白橡木    None    None
28       白色    None    None
29       白色    None    None
30       樺木    None    None
31       白色    None    None
32     染白橡木    None    None
33      黑棕色    None    None
34       白色    None    None
35       白色    None    None
36       白色    None    None
37      黑棕色    None    None
38      黑棕色    None    None
39       白色    None    None
40      黑棕色    None    None
41     染白橡木    None    None
42       棕色    None    None
43       白色    None    None
44       黑色    None    None
45       白色    None    None
46       松木    None    None
47      黑棕色    None    None
48       白色    None    None
49       白色    None    None
50       白色    None    None
51       樺木    None    None
52       白色    None    None
53       松木    None    None
54       白色    None    None
55      黑棕色    None    None
56       白色    None    None
57       鋁質    None    None
58       灰色    None    None
59       白色    None    None
60      黑棕色    None    None
61       白色    None    None
62       棕色    None    None
63       棕色    None    None
64       白色    None    None
65       白色    None    None
66       樺木    None    None
67       黑色    None    None
68       白色    None    None
69       白色    None    None
70       白色    None    None
71       灰色    None    None
72       白色    None    None
73      黑棕色    None    None
74      黑棕色    None    None
75       白色    None    None
76     染白橡木    None    None
77       白色    None    None
78       白色    None    None
79      黑棕色    None    None
80      黑棕色    None    None
81     染白橡木    None    None
82       棕色    None    None
83       白色    None    None
84       棕色    None    None
85       白色    None    None
86       白色    None    None
87       鋁質      黑色    None
88       白色    None    None
89       白色    None    None
90       白色    None    None
91      黑棕色    None    None
92     染白橡木    None    None
93       樺木    None    None
94       鋁質    None    None
95       白色    None    None
96       黑色    None    None
97      黑棕色    None    None
98     染白橡木    None    None
99       白色    None    None
100      白色    None    None
101    染白橡木    None    None
102      棕色    None    None
103      棕色    None    None
104      白色    None    None
105      白色    None    None
106      白色    None    None
107      白色    None    None
108     淺灰色    None    None
109     淺灰色    None    None
110      白色    None    None
111    染白橡木    None    None
112      白色    None    None
113      白色    None    None
114      松木    None    None
115      白色    None    None
116      白色    None    None
117     黑棕色    None    None
118      鋁質      黑色    None
119      白色    None    None
120      白色    None    None
121      白色    None    None
122      白色    None    None
123    染白橡木    None    None
124    染白橡木    None    None
125      白色    None    None
126      鋁質      藤製    None
127      松木    None    None
128      白色    None    None
129      白色     淺灰色    None
130      白色    None    None
131     深灰色    None    None
132     染白色    None    None
133      白色    None    None
134      松木    None    None
135    染白橡木    None    None
136    染白橡木    None    None
137      白色    None    None
138      黑色    None    None
139      白色    None    None
140      白色    None    None
141    染白橡木    None    None


### new_color

In [37]:
new_color_c = pd.read_csv('D:/pytel_data/outhet_excel_2/df_c_2.csv',encoding='utf8')

In [38]:
new_color_c

Unnamed: 0 Product_number color_1 color_2 color_3
0             0     004.243.63      黑色    None    None
1             1     091.838.68      白色    None    None
2             2     092.792.91      黑色    None    None
3             3     391.987.88      白色    None    None
4             4     403.201.32      白色    None    None
5             5     503.201.36      棕色    None    None
6             6     503.544.85      白色    None    None
7             7     504.544.42      藍色    None    None
8             8     591.987.87      白色    None    None
9             9     691.299.39      棕色    None    None
10           10     691.987.58      白色    None    None
11           11     703.493.27      白色    None    None
12           12     891.298.77      白色    None    None
13           13     891.299.43      白色    None    None
14           14     891.987.57      白色    None    None
15           15     892.792.92      黑色    None    None
16           16     090.191.42      白色    None    None
17           17     091.981.53      白色    None    None
18           18     091.981.67      白色    None    None
19           19     091.982.33      棕色    None    None
20           20     091.985.15      棕色    None    None
21           21     091.986.38      白色    None    None
22           22     091.998.93      白色    None    None
23           23     092.008.77      棕色    None    None
24           24     092.010.18      白色    None    None
25           25     092.772.87      白色    None    None
26           26     104.048.02      棕色    None    None
27           27     190.273.92      白色    None    None
28           28     191.981.43      白色    None    None
29           29     191.981.62      白色    None    None
30           30     191.982.18      棕色    None    None
31           31     191.997.79      白色    None    None
32           32     192.009.71      白色    None    None
33           33     192.411.65      棕色    None    None
34           34     192.412.88      白色    None    None
35           35     192.772.82      白色    None    None
36           36     291.981.52      白色    None    None
37           37     291.982.65      棕色    None    None
38           38     291.983.93      棕色    None    None
39           39     291.986.37      白色    None    None
40           40     292.006.21      棕色    None    None
41           41     292.010.17      白色    None    None
42           42     292.410.75      棕色    None    None
43           43     292.413.44      白色    None    None
44           44     292.689.13      黑色    None    None
45           45     293.030.06      白色    None    None
46           46     293.037.42      棕色    None    None
47           47     390.094.53      棕色    None    None
48           48     390.191.88      白色    None    None
49           49     391.981.42      白色    None    None
50           50     391.981.61      白色    None    None
51           51     391.982.17      棕色    None    None
52           52     391.983.97      白色    None    None
53           53     391.985.14      棕色    None    None
54           54     391.997.78      白色    None    None
55           55     392.009.08      棕色    None    None
56           56     392.412.49      白色    None    None
57           57     392.875.48     特殊色    None    None
58           58     404.463.58      灰色    None    None
59           59     491.981.51      白色    None    None
60           60     491.983.92      棕色    None    None
61           61     491.994.62      白色    None    None
62           62     492.410.60      棕色    None    None
63           63     492.411.64      棕色    None    None
64           64     492.413.43      白色    None    None
65           65     492.414.23      白色    None    None
66           66     492.475.85      棕色    None    None
67           67     492.689.12      黑色    None    None
68           68     492.772.66      白色    None    None
69           69     492.773.08      白色    None    None
70           70     493.030.29      白色    None    None
71           71     504.463.53      灰色    Non

In [39]:
df_new_color_c = new_color_c[['color_1','color_2','color_3']]

In [40]:
df_new_color_c.columns = ['new_color_1','new_color_2','new_color_3']

In [41]:
df_new_color_c

new_color_1 new_color_2 new_color_3
0            黑色        None        None
1            白色        None        None
2            黑色        None        None
3            白色        None        None
4            白色        None        None
5            棕色        None        None
6            白色        None        None
7            藍色        None        None
8            白色        None        None
9            棕色        None        None
10           白色        None        None
11           白色        None        None
12           白色        None        None
13           白色        None        None
14           白色        None        None
15           黑色        None        None
16           白色        None        None
17           白色        None        None
18           白色        None        None
19           棕色        None        None
20           棕色        None        None
21           白色        None        None
22           白色        None        None
23           棕色        None        None
24           白色        None        None
25           白色        None        None
26           棕色        None        None
27           白色        None        None
28           白色        None        None
29           白色        None        None
30           棕色        None        None
31           白色        None        None
32           白色        None        None
33           棕色        None        None
34           白色        None        None
35           白色        None        None
36           白色        None        None
37           棕色        None        None
38           棕色        None        None
39           白色        None        None
40           棕色        None        None
41           白色        None        None
42           棕色        None        None
43           白色        None        None
44           黑色        None        None
45           白色        None        None
46           棕色        None        None
47           棕色        None        None
48           白色        None        None
49           白色        None        None
50           白色        None        None
51           棕色        None        None
52           白色        None        None
53           棕色        None        None
54           白色        None        None
55           棕色        None        None
56           白色        None        None
57          特殊色        None        None
58           灰色        None        None
59           白色        None        None
60           棕色        None        None
61           白色        None        None
62           棕色        None        None
63           棕色        None        None
64           白色        None        None
65           白色        None        None
66           棕色        None        None
67           黑色        None        None
68           白色        None        None
69           白色        None        None
70           白色        None        None
71           灰色        None        None
72           白色        None        None
73           棕色        None        None
74           棕色        None        None
75           白色        None        None
76           白色        None        None
77           白色        None        None
78           白色        None        None
79           棕色        None        None
80           棕色        None        None
81           白色        None        None
82           棕色        None        None
83           白色        None        None
84           棕色        None        None
85           白色        None        None
86           白色        None        None
87          特殊色          黑色        None
88           白色        None        None
89           白色        None        None
90           白色        None        None
91           棕色        None        None
92           白色        None        None
93           棕色        None        None
94          特殊色        None        None
95           白色        None        None
96           黑色        None        None
97           棕色        None        None
98           白色        None        None
99  

### l*w*h

In [42]:
df3 = pd.read_csv('D:/pytel_data/outhet_excel_2/ikeamaster_ver7_cleaning_demension_1.csv',encoding='utf8')

In [43]:
df3

Unnamed: 0              id length length_longest length_shortest width  \
0             0  ikea004.243.63    207           None            None    88   
1             1  ikea091.838.68    207           None            None    88   
2             2  ikea092.792.91    207           None            None    88   
3             3  ikea391.987.88    205           None            None    86   
4             4  ikea403.201.32    207           None            None    88   
5             5  ikea503.201.36    207           None            None    88   
6             6  ikea503.544.85    205           None            None    86   
7             7  ikea504.544.42    203           None            None    93   
8             8  ikea591.987.87    205           None            None    86   
9             9  ikea691.299.39    207           None            None    88   
10           10  ikea691.987.58    205           None            None    86   
11           11  ikea703.493.27    209           None            None    89   
12           12  ikea891.298.77    207           None            None    88   
13           13  ikea891.299.43    207           None            None    88   
14           14  ikea891.987.57    205           None            None    86   
15           15  ikea892.792.92    207           None            None    88   
16           16  ikea090.191.42    209           None            None   196   
17           17  ikea091.981.53    206           None            None   186   
18           18  ikea091.981.67    234           None            None   186   
19           19  ikea091.982.33    211           None            None   167   
20           20  ikea091.985.15    209           None            None   160   
21           21  ikea091.986.38    210           None            None   158   
22           22  ikea091.998.93    209           None            None   166   
23           23  ikea092.008.77    209           None            None   166   
24           24  ikea092.010.18    209           None            None   196   
25           25  ikea092.772.87    209           None            None   188   
26           26  ikea104.048.02    209           None            None   166   
27           27  ikea190.273.92    209           None            None   196   
28           28  ikea191.981.43    206           None            None   158   
29           29  ikea191.981.62    234           None            None   156   
30           30  ikea191.982.18    211           None            None   164   
31           31  ikea191.997.79    209           None            None   196   
32           32  ikea192.009.71    209           None            None   196   
33           33  ikea192.411.65    207           None            None   163   
34           34  ikea192.412.88    207           None            None   163   
35           35  ikea192.772.82    209           None            None   158   
36           36  ikea291.981.52    206           None            None   186   
37           37  ikea291.982.65    211           None            None   167   
38           38  ikea291.983.93    211           None            None   194   
39           39  ikea291.986.37    210           None            None   158   
40           40  ikea292.006.21    209           None            None   166   
41           41  ikea292.010.17    209           None            None   196   
42           42  ikea292.410.75    207           None            None   163   
43           43  ikea292.413.44    207           None            None   163   
44           44  ikea292.689.13    208           None            None   158   
45           45  ikea293.030.06   2439           None            None  1417   
46           46  ikea293.037.42    205           None            None   154   
47           47  ikea390.094.53    209           None            None   196   
48           48  ikea390.191.88    209           None            None   166   
49           49  ikea391.981.42    206           None  

In [44]:
df_clearn_size_1 = df3[['length']]

In [45]:
df_clearn_size_1

length
0      207
1      207
2      207
3      205
4      207
5      207
6      205
7      203
8      205
9      207
10     205
11     209
12     207
13     207
14     205
15     207
16     209
17     206
18     234
19     211
20     209
21     210
22     209
23     209
24     209
25     209
26     209
27     209
28     206
29     234
30     211
31     209
32     209
33     207
34     207
35     209
36     206
37     211
38     211
39     210
40     209
41     209
42     207
43     207
44     208
45    2439
46     205
47     209
48     209
49     206
50     234
51     211
52     211
53     209
54     209
55     209
56     207
57     205
58     210
59     206
60     211
61     209
62     207
63     207
64     207
65     202
66     214
67     208
68     209
69     209
70    2439
71     210
72     209
73     209
74     209
75     208
76     209
77     211
78     210
79     209
80     209
81     209
82     207
83     207
84     209
85     209
86     209
87     205
88     234
89     211
90     209
91     209
92     209
93     214
94     204
95    2439
96     206
97     209
98     209
99     234
100    209
101    209
102    207
103    209
104    209
105   2439
106    244
107    202
108    206
109    206
110    208
111    209
112    234
113    211
114    209
115    209
116    209
117    209
118    205
119    209
120    244
121    209
122    206
123    209
124    209
125    207
126    205
127   None
128   None
129    207
130   None
131    207
132    213
133    209
134    209
135    209
136    209
137    207
138    206
139    209
140    209
141    211
142    207
143    202
144    209
145    209
146    206
147    209
148    211
149    209
150    209
151    205
152    211
153    207
154    205
155    209
156    209
157    211
158    209
159    207
160   None
161   None
162   None
163   None
164   None
165   None
166   None
167   None
168   None
169   None
170   None
171   None
172   None
173   None
174   None
175   None
176   None
177   None
178   None
179     90
180   None
181   None
182   None
183     90
184   None
185    118
186     75
187     92
188     90
189     75
190    140
191     55
192   None
193     58
194   None
195     90
196     95
197   None
198   None
199    118
200   None
201     90
202    118
203     90
204   None
205     90
206   None
207   None
208    140
209     40
210     64
211     95
212     50
213    118
214    120
215     50
216   None
217   None
218   None
219   None
220     92
221   None
222    120
223    115
224   None
225     50
226   None
227     40
228     50
229     98
230   None
231     72
232   None
233     75
234   None
235     90
236   None
237     75
238     75
239   None
240   None
241    118
242    100
243   None
244    100
245   None
246     50
247   None
248     70
249    180
250    100
251    100
252   None
253     90
254   None
255     55
256   None
257   None
258   None
259   None
260   None
261   None
262   None
263   None
264   None
265   None
266   None
267   None
268   None
269   None
270   None
271   None
272   None
273   None
274   None
275   None
276   None
277   None
278   None
279   None
280   None
281   None
282   None
283    103
284   None
285   None
286    105
287   None
288   None
289   None
290   None
291   None
292   None
293   None
294   None
295   None
296   None
297   None
298   None
299   None
300   None
301   None
302   None
303   None
304   None
305   None
306   None
307   None
308   None
309   None
310   None
311   None
312   None
313   None
314    105
315   None
316   None
317   None
318   None
319   None
320   None
321   None
322   None
323   None
324   None
325    125
326    155
327   None
328   None
329    125
330    140
331    140
332    110
333    140
334   None
335   None
336    140
337    155
338   None
339   None
340   None
341   None
342    155
343   None
344    140
345    140
346   None
347    118
348    160
349   None
350    125
351     74
352    130
353   None
354    118
355   None
356   None
357     75
358    140
359   None
360     74
361   None
362   None


In [46]:
df_clearn_size_1['length'] = df_clearn_size_1['length'].str.replace('None', '0') 

<ipython-input-46-c98350e2e341>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clearn_size_1['length'] = df_clearn_size_1['length'].str.replace('None', '0')


In [47]:
df_clearn_size_1

length
0      207
1      207
2      207
3      205
4      207
5      207
6      205
7      203
8      205
9      207
10     205
11     209
12     207
13     207
14     205
15     207
16     209
17     206
18     234
19     211
20     209
21     210
22     209
23     209
24     209
25     209
26     209
27     209
28     206
29     234
30     211
31     209
32     209
33     207
34     207
35     209
36     206
37     211
38     211
39     210
40     209
41     209
42     207
43     207
44     208
45    2439
46     205
47     209
48     209
49     206
50     234
51     211
52     211
53     209
54     209
55     209
56     207
57     205
58     210
59     206
60     211
61     209
62     207
63     207
64     207
65     202
66     214
67     208
68     209
69     209
70    2439
71     210
72     209
73     209
74     209
75     208
76     209
77     211
78     210
79     209
80     209
81     209
82     207
83     207
84     209
85     209
86     209
87     205
88     234
89     211
90     209
91     209
92     209
93     214
94     204
95    2439
96     206
97     209
98     209
99     234
100    209
101    209
102    207
103    209
104    209
105   2439
106    244
107    202
108    206
109    206
110    208
111    209
112    234
113    211
114    209
115    209
116    209
117    209
118    205
119    209
120    244
121    209
122    206
123    209
124    209
125    207
126    205
127      0
128      0
129    207
130      0
131    207
132    213
133    209
134    209
135    209
136    209
137    207
138    206
139    209
140    209
141    211
142    207
143    202
144    209
145    209
146    206
147    209
148    211
149    209
150    209
151    205
152    211
153    207
154    205
155    209
156    209
157    211
158    209
159    207
160      0
161      0
162      0
163      0
164      0
165      0
166      0
167      0
168      0
169      0
170      0
171      0
172      0
173      0
174      0
175      0
176      0
177      0
178      0
179     90
180      0
181      0
182      0
183     90
184      0
185    118
186     75
187     92
188     90
189     75
190    140
191     55
192      0
193     58
194      0
195     90
196     95
197      0
198      0
199    118
200      0
201     90
202    118
203     90
204      0
205     90
206      0
207      0
208    140
209     40
210     64
211     95
212     50
213    118
214    120
215     50
216      0
217      0
218      0
219      0
220     92
221      0
222    120
223    115
224      0
225     50
226      0
227     40
228     50
229     98
230      0
231     72
232      0
233     75
234      0
235     90
236      0
237     75
238     75
239      0
240      0
241    118
242    100
243      0
244    100
245      0
246     50
247      0
248     70
249    180
250    100
251    100
252      0
253     90
254      0
255     55
256      0
257      0
258      0
259      0
260      0
261      0
262      0
263      0
264      0
265      0
266      0
267      0
268      0
269      0
270      0
271      0
272      0
273      0
274      0
275      0
276      0
277      0
278      0
279      0
280      0
281      0
282      0
283    103
284      0
285      0
286    105
287      0
288      0
289      0
290      0
291      0
292      0
293      0
294      0
295      0
296      0
297      0
298      0
299      0
300      0
301      0
302      0
303      0
304      0
305      0
306      0
307      0
308      0
309      0
310      0
311      0
312      0
313      0
314    105
315      0
316      0
317      0
318      0
319      0
320      0
321      0
322      0
323      0
324      0
325    125
326    155
327      0
328      0
329    125
330    140
331    140
332    110
333    140
334      0
335      0
336    140
337    155
338      0
339      0
340      0
341      0
342    155
343      0
344    140
345    140
346      0
347    118
348    160
349      0
350    125
351     74
352    130
353      0
354    118
355      0
356      0
357     75
358    140
359      0
360     74
361      0
362      0


In [48]:
df_clearn_size_2 = df3[['length_longest']]

In [49]:
df_clearn_size_2['length_longest'] = df_clearn_size_2['length_longest'].str.replace('None', '0') 

<ipython-input-49-ff0c21396a51>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clearn_size_2['length_longest'] = df_clearn_size_2['length_longest'].str.replace('None', '0')


In [50]:
df_clearn_size_2

length_longest
0                0
1                0
2                0
3                0
4                0
5                0
6                0
7                0
8                0
9                0
10               0
11               0
12               0
13               0
14               0
15               0
16               0
17               0
18               0
19               0
20               0
21               0
22               0
23               0
24               0
25               0
26               0
27               0
28               0
29               0
30               0
31               0
32               0
33               0
34               0
35               0
36               0
37               0
38               0
39               0
40               0
41               0
42               0
43               0
44               0
45               0
46               0
47               0
48               0
49               0
50               0
51               0
52               0
53               0
54               0
55               0
56               0
57               0
58               0
59               0
60               0
61               0
62               0
63               0
64               0
65               0
66               0
67               0
68               0
69               0
70               0
71               0
72               0
73               0
74               0
75               0
76               0
77               0
78               0
79               0
80               0
81               0
82               0
83               0
84               0
85               0
86               0
87               0
88               0
89               0
90               0
91               0
92               0
93               0
94               0
95               0
96               0
97               0
98               0
99               0
100              0
101              0
102              0
103              0
104              0
105              0
106              0
107              0
108              0
109              0
110              0
111              0
112              0
113              0
114              0
115              0
116              0
117              0
118              0
119              0
120              0
121              0
122              0
123              0
124              0
125              0
126              0
127              0
128              0
129              0
130              0
131              0
132              0
133              0
134              0
135              0
136              0
137              0
138              0
139              0
140              0
141              0
142              0
143              0
144              0
145              0
146              0
147              0
148              0
149              0
150              0
151              0
152              0
153              0
154              0
155              0
156              0
157              0
158              0
159              0
160              0
161              0
162              0
163              0
164              0
165              0
166              0
167              0
168              0
169              0
170              0
171              0
172              0
173              0
174              0
175              0
176              0
177              0
178              0
179              0
180              0
181              0
182              0
183              0
184              0
185              0
186              0
187              0
188              0
189              0
190              0
191              0
192              0
193              0
194              0
195              0
196              0
197              0
198              0
199              0
200              0
201              0
202              0
203              0
204              0
205              0
206              0
207              0
208              0
209           

In [51]:
df_clearn_size_3 = df3[['length_shortest']]

In [52]:
df_clearn_size_3['length_shortest'] = df_clearn_size_3['length_shortest'].str.replace('None', '0') 

<ipython-input-52-5ac493bf3c3b>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clearn_size_3['length_shortest'] = df_clearn_size_3['length_shortest'].str.replace('None', '0')


In [53]:
df_clearn_size_3

length_shortest
0                 0
1                 0
2                 0
3                 0
4                 0
5                 0
6                 0
7                 0
8                 0
9                 0
10                0
11                0
12                0
13                0
14                0
15                0
16                0
17                0
18                0
19                0
20                0
21                0
22                0
23                0
24                0
25                0
26                0
27                0
28                0
29                0
30                0
31                0
32                0
33                0
34                0
35                0
36                0
37                0
38                0
39                0
40                0
41                0
42                0
43                0
44                0
45                0
46                0
47                0
48                0
49                0
50                0
51                0
52                0
53                0
54                0
55                0
56                0
57                0
58                0
59                0
60                0
61                0
62                0
63                0
64                0
65                0
66                0
67                0
68                0
69                0
70                0
71                0
72                0
73                0
74                0
75                0
76                0
77                0
78                0
79                0
80                0
81                0
82                0
83                0
84                0
85                0
86                0
87                0
88                0
89                0
90                0
91                0
92                0
93                0
94                0
95                0
96                0
97                0
98                0
99                0
100               0
101               0
102               0
103               0
104               0
105               0
106               0
107               0
108               0
109               0
110               0
111               0
112               0
113               0
114               0
115               0
116               0
117               0
118               0
119               0
120               0
121               0
122               0
123               0
124               0
125               0
126               0
127               0
128               0
129               0
130               0
131               0
132               0
133               0
134               0
135               0
136               0
137               0
138               0
139               0
140               0
141               0
142               0
143               0
144               0
145               0
146               0
147               0
148               0
149               0
150               0
151               0
152               0
153               0
154               0
155               0
156               0
157               0
158               0
159               0
160               0
161               0
162               0
163               0
164               0
165               0
166               0
167               0
168               0
169               0
170               0
171               0
172               0
173               0
174               0
175               0
176               0
177               0
178               0
179               0
180               0
181               0
182               0
183               0
184               0
185               0
186               0
187               0
188               0
189               0
190               0
191               0
192               0
193               0
194               0
195               0
196               0
197               0
198               0
199 

In [54]:
df_clearn_size_4 = df3[['width']]

In [55]:
df_clearn_size_4['width'] = df_clearn_size_4['width'].str.replace('None', '0') 

<ipython-input-55-046ea93e2232>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clearn_size_4['width'] = df_clearn_size_4['width'].str.replace('None', '0')


In [56]:
df_clearn_size_4

width
0      88
1      88
2      88
3      86
4      88
5      88
6      86
7      93
8      86
9      88
10     86
11     89
12     88
13     88
14     86
15     88
16    196
17    186
18    186
19    167
20    160
21    158
22    166
23    166
24    196
25    188
26    166
27    196
28    158
29    156
30    164
31    196
32    196
33    163
34    163
35    158
36    186
37    167
38    194
39    158
40    166
41    196
42    163
43    163
44    158
45   1417
46    154
47    196
48    166
49    158
50    156
51    164
52    167
53    160
54    196
55    196
56    163
57    154
58    188
59    186
60    194
61    166
62    163
63    163
64    163
65    240
66    170
67    158
68    158
69    188
70   1401
71    158
72    196
73    196
74    166
75    157
76    196
77    167
78    158
79    166
80    196
81    166
82    163
83    163
84    159
85    159
86    158
87    194
88    186
89    194
90    196
91    196
92    166
93    170
94    194
95   1401
96    154
97    166
98    166
99    156
100   166
101   166
102   163
103   159
104   159
105  1417
106   140
107   160
108   154
109   184
110   157
111   166
112   186
113   194
114   160
115   166
116   196
117   166
118   154
119   166
120   140
121   166
122   158
123   196
124   166
125   163
126   194
127     0
128     0
129    97
130     0
131   965
132   152
133   105
134   128
135   105
136   105
137   103
138    94
139   135
140   135
141   135
142   103
143    92
144    98
145   105
146    94
147   135
148   104
149   135
150    98
151    83
152   135
153   103
154    94
155   105
156   105
157   104
158   128
159   103
160    46
161     0
162    45
163    37
164    45
165    46
166    45
167    48
168    51
169    45
170    39
171    76
172  1003
173   100
174   120
175     0
176     0
177     0
178     0
179    55
180     0
181     0
182     0
183    90
184     0
185    50
186    60
187    38
188    90
189    60
190    60
191    55
192     0
193    38
194     0
195    55
196    95
197     0
198     0
199    78
200     0
201    46
202    60
203    90
204     0
205    55
206     0
207     0
208    60
209    40
210    64
211    95
212    50
213    78
214    40
215    50
216     0
217     0
218     0
219     0
220    38
221     0
222    40
223    58
224    50
225    50
226     0
227    40
228    50
229    50
230     0
231    47
232     0
233    60
234     0
235    55
236     0
237    60
238    60
239     0
240     0
241    78
242    75
243     0
244    75
245     0
246    50
247    65
248    70
249    59
250    75
251    35
252     0
253    55
254     0
255    55
256    40
257    54
258    40
259    50
260    60
261    40
262    43
263    39
264    49
265    41
266     0
267    49
268    51
269    45
270    55
271    43
272    47
273    42
274    49
275    60
276    47
277    69
278    54
279    43
280    43
281    45
282    42
283    29
284    45
285    49
286    36
287    42
288    45
289    42
290    44
291    50
292    43
293    45
294    44
295    53
296    42
297    42
298    49
299    53
300    51
301    51
302    57
303    39
304    57
305    46
306    44
307    58
308    53
309    50
310    43
311    42
312    42
313    39
314    36
315    43
316    44
317    51
318    40
319    39
320    42
321    40
322    40
323    44
324    42
325    75
326     0
327     0
328   105
329    75
330    78
331    85
332    87
333    78
334    95
335     0
336    78
337     0
338   105
339    95
340     0
341     0
342    87
343     0
344    85
345    78
346    95
347    74
348    95
349     0
350    75
351    74
352    80
353    74
354    74
355     0
356     0
357    75
358    78
359    74
360    74
361     0
362     0
363     0
364    75
365    75
366     0
367    80
368    80
369    95
370     0
371     0
372    85
373    87
374    80
375    80
376    95
377    85
378    85
379     0
380     0
381     0
382     0
383     0
384    85
385    78
386    75
387    78
388     0
389    78
390     0
391    74
392     0
393    80
394     0
395    80
396    79
397    80
398     0
399 

In [57]:
df_clearn_size_5 = df3[['width_smallest']]

In [58]:
df_clearn_size_5['width_smallest'] = df_clearn_size_5['width_smallest'].str.replace('None', '0') 

<ipython-input-58-96b58161ddf3>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clearn_size_5['width_smallest'] = df_clearn_size_5['width_smallest'].str.replace('None', '0')


In [59]:
df_clearn_size_5

width_smallest
0                0
1                0
2                0
3                0
4                0
5                0
6                0
7                0
8                0
9                0
10               0
11               0
12               0
13               0
14               0
15               0
16               0
17               0
18               0
19               0
20               0
21               0
22               0
23               0
24               0
25               0
26               0
27               0
28               0
29               0
30               0
31               0
32               0
33               0
34               0
35               0
36               0
37               0
38               0
39               0
40               0
41               0
42               0
43               0
44               0
45               0
46               0
47               0
48               0
49               0
50               0
51               0
52               0
53               0
54               0
55               0
56               0
57               0
58               0
59               0
60               0
61               0
62               0
63               0
64               0
65               0
66               0
67               0
68               0
69               0
70               0
71               0
72               0
73               0
74               0
75               0
76               0
77               0
78               0
79               0
80               0
81               0
82               0
83               0
84               0
85               0
86               0
87               0
88               0
89               0
90               0
91               0
92               0
93               0
94               0
95               0
96               0
97               0
98               0
99               0
100              0
101              0
102              0
103              0
104              0
105              0
106              0
107              0
108              0
109              0
110              0
111              0
112              0
113              0
114              0
115              0
116              0
117              0
118              0
119              0
120              0
121              0
122              0
123              0
124              0
125              0
126              0
127              0
128              0
129              0
130              0
131              0
132              0
133              0
134              0
135              0
136              0
137              0
138              0
139              0
140              0
141              0
142              0
143              0
144              0
145              0
146              0
147              0
148              0
149              0
150              0
151              0
152              0
153              0
154              0
155              0
156              0
157              0
158              0
159              0
160              0
161              0
162              0
163              0
164              0
165              0
166              0
167              0
168              0
169              0
170              0
171              0
172              0
173              0
174              0
175              0
176              0
177              0
178              0
179              0
180              0
181              0
182              0
183              0
184              0
185              0
186              0
187              0
188              0
189              0
190              0
191              0
192              0
193              0
194              0
195              0
196              0
197              0
198              0
199              0
200              0
201              0
202              0
203              0
204              0
205              0
206              0
207              0
208              0
209           

In [60]:
df_clearn_size_6 = df3[['width_widest']]

In [61]:
df_clearn_size_6['width_widest'] = df_clearn_size_6['width_widest'].str.replace('None', '0') 

<ipython-input-61-0dc80936ad0f>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clearn_size_6['width_widest'] = df_clearn_size_6['width_widest'].str.replace('None', '0')


In [62]:
df_clearn_size_6

width_widest
0              0
1              0
2              0
3              0
4              0
5              0
6              0
7              0
8              0
9              0
10             0
11             0
12             0
13             0
14             0
15             0
16             0
17             0
18             0
19             0
20             0
21             0
22             0
23             0
24             0
25             0
26             0
27             0
28             0
29             0
30             0
31             0
32             0
33             0
34             0
35             0
36             0
37             0
38             0
39             0
40             0
41             0
42             0
43             0
44             0
45             0
46             0
47             0
48             0
49             0
50             0
51             0
52             0
53             0
54             0
55             0
56             0
57             0
58             0
59             0
60             0
61             0
62             0
63             0
64             0
65             0
66             0
67             0
68             0
69             0
70             0
71             0
72             0
73             0
74             0
75             0
76             0
77             0
78             0
79             0
80             0
81             0
82             0
83             0
84             0
85             0
86             0
87             0
88             0
89             0
90             0
91             0
92             0
93             0
94             0
95             0
96             0
97             0
98             0
99             0
100            0
101            0
102            0
103            0
104            0
105            0
106            0
107            0
108            0
109            0
110            0
111            0
112            0
113            0
114            0
115            0
116            0
117            0
118            0
119            0
120            0
121            0
122            0
123            0
124            0
125            0
126            0
127            0
128            0
129            0
130            0
131            0
132            0
133            0
134            0
135            0
136            0
137            0
138            0
139            0
140            0
141            0
142            0
143            0
144            0
145            0
146            0
147            0
148            0
149            0
150            0
151            0
152            0
153            0
154            0
155            0
156            0
157            0
158            0
159            0
160            0
161            0
162            0
163            0
164            0
165            0
166            0
167            0
168            0
169            0
170            0
171            0
172            0
173            0
174            0
175            0
176            0
177            0
178            0
179            0
180            0
181            0
182            0
183            0
184            0
185            0
186            0
187            0
188            0
189            0
190            0
191            0
192            0
193            0
194            0
195            0
196            0
197            0
198            0
199            0
200            0
201            0
202            0
203            0
204            0
205            0
206            0
207            0
208            0
209            0
210            0
211            0
212            0
213            0
214            0
215            0
216            0
217            0
218            0
219            0
220            0
221            0
222            0
223            0
224            0
225            0
226            0
227            0
228            0
229            0
230            0
231            0
232            0
233            0
234      

In [63]:
df_clearn_size_7 = df3[['height']]

In [64]:
df_clearn_size_7['height'] = df_clearn_size_7['height'].str.replace('None', '0') 

<ipython-input-64-2999f87e0bad>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clearn_size_7['height'] = df_clearn_size_7['height'].str.replace('None', '0')


In [65]:
df_clearn_size_7

height
0       94
1       86
2       94
3       57
4       86
5       86
6       57
7       27
8       57
9       86
10      57
11      83
12      86
13      86
14      57
15      94
16       0
17      47
18     111
19       0
20       0
21       0
22       0
23       0
24       0
25       0
26       0
27       0
28      47
29     111
30       0
31       0
32       0
33       0
34       0
35       0
36      47
37       0
38       0
39       0
40       0
41       0
42       0
43       0
44     140
45      43
46       0
47       0
48       0
49      47
50     111
51       0
52       0
53       0
54       0
55       0
56       0
57      99
58       0
59      47
60       0
61       0
62       0
63       0
64       0
65      30
66      43
67     140
68       0
69       0
70      43
71       0
72       0
73       0
74       0
75       0
76       0
77       0
78       0
79       0
80       0
81       0
82       0
83       0
84       0
85       0
86       0
87      99
88     111
89       0
90       0
91       0
92       0
93      43
94      29
95      43
96       0
97       0
98       0
99     111
100      0
101      0
102      0
103      0
104      0
105    426
106     43
107     30
108      0
109      0
110      0
111      0
112    111
113      0
114      0
115      0
116      0
117      0
118     99
119      0
120     43
121      0
122     47
123      0
124      0
125      0
126     99
127    157
128    157
129    162
130    182
131   1305
132    214
133      0
134      0
135      0
136      0
137      0
138      0
139      0
140      0
141      0
142      0
143     55
144      0
145      0
146      0
147      0
148      0
149      0
150      0
151     23
152      0
153      0
154      0
155      0
156      0
157      0
158      0
159      0
160     70
161     74
162    580
163     45
164     65
165     70
166    580
167     69
168     59
169     53
170     53
171     79
172     78
173    159
174     78
175     45
176     45
177      0
178     48
179     48
180     53
181     53
182      0
183     46
184      0
185     50
186     48
187     71
188     46
189     48
190     45
191     45
192     48
193     58
194     45
195     45
196     31
197     63
198     56
199     45
200      0
201     46
202     45
203     46
204     48
205     48
206      0
207      0
208     45
209     60
210     45
211     31
212     66
213     45
214     40
215     45
216     53
217     47
218     40
219     48
220     71
221      0
222     40
223     47
224     50
225     45
226     45
227     60
228     45
229     50
230     60
231      0
232      0
233     48
234      0
235     45
236     48
237     50
238     50
239      0
240      0
241     45
242     48
243     45
244     48
245      0
246     45
247     52
248     50
249     40
250     48
251     63
252     53
253     45
254     60
255     45
256    101
257     90
258     88
259     95
260    100
261    101
262    114
263     74
264     77
265     90
266      0
267     83
268     97
269     76
270     83
271     91
272     83
273     85
274     77
275     82
276     89
277      0
278     76
279     95
280     95
281     81
282     80
283     45
284     76
285     81
286     45
287     95
288     81
289     95
290     77
291     76
292     95
293     81
294    100
295     87
296     95
297     85
298     81
299     84
300     97
301     97
302     82
303     77
304     99
305     80
306     97
307     85
308     84
309     76
310     95
311     90
312     85
313     77
314     45
315     91
316     97
317     97
318      0
319     45
320     45
321      0
322      0
323     45
324     45
325     72
326     74
327      0
328      0
329     74
330     74
331     74
332     74
333     74
334      0
335      0
336     74
337      0
338      0
339      0
340      0
341      0
342     74
343      0
344      0
345     74
346      0
347     73
348      0
349      0
350     74
351      0
352      0
353      0
354     73
355      0
356      0
357     74
358     74
359      0
360     73
361      0
362      0


In [66]:
df_clearn_size_8 = df3[['height_lowest']]

In [67]:
df_clearn_size_8['height_lowest'] = df_clearn_size_8['height_lowest'].str.replace('None', '0') 

<ipython-input-67-1271f024672c>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clearn_size_8['height_lowest'] = df_clearn_size_8['height_lowest'].str.replace('None', '0')


In [68]:
df_clearn_size_8

height_lowest
0               0
1               0
2               0
3               0
4               0
5               0
6               0
7               0
8               0
9               0
10              0
11              0
12              0
13              0
14              0
15              0
16              0
17              0
18              0
19              0
20              0
21              0
22              0
23              0
24              0
25              0
26              0
27              0
28              0
29              0
30              0
31              0
32              0
33              0
34              0
35              0
36              0
37              0
38              0
39              0
40              0
41              0
42              0
43              0
44              0
45              0
46              0
47              0
48              0
49              0
50              0
51              0
52              0
53              0
54              0
55              0
56              0
57              0
58              0
59              0
60              0
61              0
62              0
63              0
64              0
65              0
66              0
67              0
68              0
69              0
70              0
71              0
72              0
73              0
74              0
75              0
76              0
77              0
78              0
79              0
80              0
81              0
82              0
83              0
84              0
85              0
86              0
87              0
88              0
89              0
90              0
91              0
92              0
93              0
94              0
95              0
96              0
97              0
98              0
99              0
100             0
101             0
102             0
103             0
104             0
105             0
106             0
107             0
108             0
109             0
110             0
111             0
112             0
113             0
114             0
115             0
116             0
117             0
118             0
119             0
120             0
121             0
122             0
123             0
124             0
125             0
126             0
127             0
128             0
129             0
130             0
131             0
132             0
133             0
134             0
135             0
136             0
137             0
138             0
139             0
140             0
141             0
142             0
143             0
144             0
145             0
146             0
147             0
148             0
149             0
150             0
151             0
152             0
153             0
154             0
155             0
156             0
157             0
158             0
159             0
160             0
161             0
162             0
163             0
164             0
165             0
166             0
167             0
168             0
169             0
170             0
171             0
172             0
173             0
174             0
175             0
176             0
177             0
178             0
179             0
180             0
181             0
182             0
183             0
184             0
185             0
186             0
187             0
188             0
189             0
190             0
191             0
192             0
193             0
194             0
195             0
196             0
197             0
198             0
199             0
200             0
201             0
202             0
203             0
204             0
205             0
206             0
207             0
208             0
209             0
210             0
211             0
212             0
213             0
214             0
215             0
216             0
217             0
218             0
219             0
220             0
221     

In [69]:
df_clearn_size_9 = df3[['height_highest']]
df_clearn_size_9['height_highest'] = df_clearn_size_9['height_highest'].str.replace('None', '0') 
df_clearn_size_9

<ipython-input-69-851f022726be>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clearn_size_9['height_highest'] = df_clearn_size_9['height_highest'].str.replace('None', '0')


height_highest
0                0
1                0
2                0
3                0
4                0
5                0
6                0
7                0
8                0
9                0
10               0
11               0
12               0
13               0
14               0
15               0
16               0
17               0
18               0
19               0
20               0
21               0
22               0
23               0
24               0
25               0
26               0
27               0
28               0
29               0
30               0
31               0
32               0
33               0
34               0
35               0
36               0
37               0
38               0
39               0
40               0
41               0
42               0
43               0
44               0
45               0
46               0
47               0
48               0
49               0
50               0
51               0
52               0
53               0
54               0
55               0
56               0
57               0
58               0
59               0
60               0
61               0
62               0
63               0
64               0
65               0
66               0
67               0
68               0
69               0
70               0
71               0
72               0
73               0
74               0
75               0
76               0
77               0
78               0
79               0
80               0
81               0
82               0
83               0
84               0
85               0
86               0
87               0
88               0
89               0
90               0
91               0
92               0
93               0
94               0
95               0
96               0
97               0
98               0
99               0
100              0
101              0
102              0
103              0
104              0
105              0
106              0
107              0
108              0
109              0
110              0
111              0
112              0
113              0
114              0
115              0
116              0
117              0
118              0
119              0
120              0
121              0
122              0
123              0
124              0
125              0
126              0
127              0
128              0
129              0
130              0
131              0
132              0
133              0
134              0
135              0
136              0
137              0
138              0
139              0
140              0
141              0
142              0
143              0
144              0
145              0
146              0
147              0
148              0
149              0
150              0
151              0
152              0
153              0
154              0
155              0
156              0
157              0
158              0
159              0
160              0
161              0
162              0
163              0
164              0
165              0
166              0
167              0
168              0
169              0
170              0
171              0
172              0
173              0
174              0
175              0
176              0
177              0
178              0
179              0
180              0
181              0
182              0
183              0
184              0
185              0
186              0
187              0
188              0
189              0
190              0
191              0
192              0
193              0
194              0
195              0
196              0
197              0
198              0
199              0
200              0
201              0
202              0
203              0
204              0
205              0
206              0
207              0
208              0
209           

In [70]:
df3_2 = pd.concat([df_clearn_size_1, df_clearn_size_2, df_clearn_size_3, df_clearn_size_4, df_clearn_size_5, df_clearn_size_6, df_clearn_size_7, df_clearn_size_8, df_clearn_size_9,], axis=1)

In [71]:
df3_2

length length_longest length_shortest width width_smallest width_widest  \
0      207              0               0    88              0            0   
1      207              0               0    88              0            0   
2      207              0               0    88              0            0   
3      205              0               0    86              0            0   
4      207              0               0    88              0            0   
5      207              0               0    88              0            0   
6      205              0               0    86              0            0   
7      203              0               0    93              0            0   
8      205              0               0    86              0            0   
9      207              0               0    88              0            0   
10     205              0               0    86              0            0   
11     209              0               0    89              0            0   
12     207              0               0    88              0            0   
13     207              0               0    88              0            0   
14     205              0               0    86              0            0   
15     207              0               0    88              0            0   
16     209              0               0   196              0            0   
17     206              0               0   186              0            0   
18     234              0               0   186              0            0   
19     211              0               0   167              0            0   
20     209              0               0   160              0            0   
21     210              0               0   158              0            0   
22     209              0               0   166              0            0   
23     209              0               0   166              0            0   
24     209              0               0   196              0            0   
25     209              0               0   188              0            0   
26     209              0               0   166              0            0   
27     209              0               0   196              0            0   
28     206              0               0   158              0            0   
29     234              0               0   156              0            0   
30     211              0               0   164              0            0   
31     209              0               0   196              0            0   
32     209              0               0   196              0            0   
33     207              0               0   163              0            0   
34     207              0               0   163              0            0   
35     209              0               0   158              0            0   
36     206              0               0   186              0            0   
37     211              0               0   167              0            0   
38     211              0               0   194              0            0   
39     210              0               0   158              0            0   
40     209              0               0   166              0            0   
41     209              0               0   196              0            0   
42     207              0               0   163              0            0   
43     207              0               0   163              0            0   
44     208              0               0   158              0            0   
45    2439              0               0  1417              0            0   
46     205              0               0   154              0            0   
47     209              0               0   196              0            0   
48     209              0               0   166              0            0   
49     206              0               0   158       

In [72]:
df_clearn_size_remix = df3_2[['length', 'length_longest', 'length_shortest', 'width', 'width_smallest', 'width_widest', 'height', 'height_lowest', 'height_highest']]

In [73]:
df_clearn_size_remix

length length_longest length_shortest width width_smallest width_widest  \
0      207              0               0    88              0            0   
1      207              0               0    88              0            0   
2      207              0               0    88              0            0   
3      205              0               0    86              0            0   
4      207              0               0    88              0            0   
5      207              0               0    88              0            0   
6      205              0               0    86              0            0   
7      203              0               0    93              0            0   
8      205              0               0    86              0            0   
9      207              0               0    88              0            0   
10     205              0               0    86              0            0   
11     209              0               0    89              0            0   
12     207              0               0    88              0            0   
13     207              0               0    88              0            0   
14     205              0               0    86              0            0   
15     207              0               0    88              0            0   
16     209              0               0   196              0            0   
17     206              0               0   186              0            0   
18     234              0               0   186              0            0   
19     211              0               0   167              0            0   
20     209              0               0   160              0            0   
21     210              0               0   158              0            0   
22     209              0               0   166              0            0   
23     209              0               0   166              0            0   
24     209              0               0   196              0            0   
25     209              0               0   188              0            0   
26     209              0               0   166              0            0   
27     209              0               0   196              0            0   
28     206              0               0   158              0            0   
29     234              0               0   156              0            0   
30     211              0               0   164              0            0   
31     209              0               0   196              0            0   
32     209              0               0   196              0            0   
33     207              0               0   163              0            0   
34     207              0               0   163              0            0   
35     209              0               0   158              0            0   
36     206              0               0   186              0            0   
37     211              0               0   167              0            0   
38     211              0               0   194              0            0   
39     210              0               0   158              0            0   
40     209              0               0   166              0            0   
41     209              0               0   196              0            0   
42     207              0               0   163              0            0   
43     207              0               0   163              0            0   
44     208              0               0   158              0            0   
45    2439              0               0  1417              0            0   
46     205              0               0   154              0            0   
47     209              0               0   196              0            0   
48     209              0               0   166              0            0   
49     206              0               0   158       

In [74]:
# size = df['size']

In [75]:
# str = size[0].replace(":", "").replace("[", "").replace("]", "").replace("{", "").replace("}", "").replace(",", "").replace("'", "").replace("產品尺寸", "")
# str.split(" ")
# print(type(str.split(" ")))
# aaa = str.split(" ")

# if "桌子最小長度" in aaa:
#     print('yes')
#     print(aaa.index("桌子最小長度"))
#     print(aaa[aaa.index("桌子最小長度")+1])

# #     "xyz 索引位置: ", aList.index( 'xyz' )

In [76]:
# print(size)

In [77]:
# # 長度

# length = []

# for i in range(len(size)):
#     str = size[i].replace(":", "").replace("[", "").replace("]", "").replace("{", "").replace("}", "").replace(",", "").replace("'", "").replace("產品尺寸", "")
#     str.split(" ")
#     s = str.split(" ")
# #     print(s)
# #     print("="*20)
    
     
#     if "長度" in s:            
#         length.append(s[s.index("長度")+1])
    
#     elif "長度" not in s:            
#         length.append('None')

In [78]:
# length

In [79]:
# # 最長長度

# length_longest = []

# for i in range(len(size)):
#     str = size[i].replace(":", "").replace("[", "").replace("]", "").replace("{", "").replace("}", "").replace(",", "").replace("'", "").replace("產品尺寸", "")
#     str.split(" ")
#     s = str.split(" ")
# #     print(s)
# #     print("="*20)
    
     
#     if "最長長度" in s:            
#         length_longest.append(s[s.index("最長長度")+1])
    
#     elif "最長長度" not in s:            
#         length_longest.append('None')

In [80]:
# length_longest

In [81]:
# # 最短長度

# length_shortest = []

# for i in range(len(size)):
#     str = size[i].replace(":", "").replace("[", "").replace("]", "").replace("{", "").replace("}", "").replace(",", "").replace("'", "").replace("產品尺寸", "")
#     str.split(" ")
#     s = str.split(" ")
# #     print(s)
# #     print("="*20)
    
     
#     if "最短長度" in s:            
#         length_shortest.append(s[s.index("最短長度")+1])
    
#     elif "最短長度" not in s:            
#         length_shortest.append('None')
    


In [82]:
# length_shortest 

In [83]:
# # 寬度

# width = []

# for i in range(len(size)):
#     str = size[i].replace(":", "").replace("[", "").replace("]", "").replace("{", "").replace("}", "").replace(",", "").replace("'", "").replace("產品尺寸", "")
#     str.split(" ")
#     s = str.split(" ")
# #     print(s)
# #     print("="*20)
    
     
#     if "寬度" in s:            
#         width.append(s[s.index("寬度")+1])
    
#     elif "寬度" not in s:            
#         width.append('None')
    


In [84]:
# width

In [85]:
# # 最小寬度

# width_smallest = []

# for i in range(len(size)):
#     str = size[i].replace(":", "").replace("[", "").replace("]", "").replace("{", "").replace("}", "").replace(",", "").replace("'", "").replace("產品尺寸", "")
#     str.split(" ")
#     s = str.split(" ")
# #     print(s)
# #     print("="*20)
    
     
#     if "最小寬度" in s:            
#         width_smallest.append(s[s.index("最小寬度")+1])
    
#     elif "最小寬度" not in s:            
#         width_smallest.append('None')
    


In [86]:
# width_smallest

In [87]:
# # 最寬寬度

# width_widest = []

# for i in range(len(size)):
#     str = size[i].replace(":", "").replace("[", "").replace("]", "").replace("{", "").replace("}", "").replace(",", "").replace("'", "").replace("產品尺寸", "")
#     str.split(" ")
#     s = str.split(" ")
# #     print(s)
# #     print("="*20)
    
     
#     if "最寬寬度" in s:            
#         width_widest.append(s[s.index("最寬寬度")+1])
    
#     elif "最寬寬度" not in s:            
#         width_widest.append('None')
    


In [88]:
# width_widest

In [89]:
# # 高度

# height = []

# for i in range(len(size)):
#     str = size[i].replace(":", "").replace("[", "").replace("]", "").replace("{", "").replace("}", "").replace(",", "").replace("'", "").replace("產品尺寸", "")
#     str.split(" ")
#     s = str.split(" ")
# #     print(s)
# #     print("="*20)
    
     
#     if "高度" in s:            
#         height.append(s[s.index("高度")+1])
    
#     elif "高度" not in s:            
#         height.append('None')

In [90]:
# height

In [91]:
# # 最低高度

# height_lowest = []

# for i in range(len(size)):
#     str = size[i].replace(":", "").replace("[", "").replace("]", "").replace("{", "").replace("}", "").replace(",", "").replace("'", "").replace("產品尺寸", "")
#     str.split(" ")
#     s = str.split(" ")
# #     print(s)
# #     print("="*20)
    
     
#     if "最低高度" in s:            
#         height_lowest.append(s[s.index("最低高度")+1])
    
#     elif "最低高度" not in s:            
#         height_lowest.append('None')
    


In [92]:
# height_lowest 

In [93]:
# # 最高高度

# height_highest = []

# for i in range(len(size)):
#     str = size[i].replace(":", "").replace("[", "").replace("]", "").replace("{", "").replace("}", "").replace(",", "").replace("'", "").replace("產品尺寸", "")
#     str.split(" ")
#     s = str.split(" ")
# #     print(s)
# #     print("="*20)
    
     
#     if "最高高度" in s:            
#         height_highest.append(s[s.index("最高高度")+1])
    
#     elif "最高高度" not in s:            
#         height_highest.append('None')
    


In [94]:
# height_highest

In [95]:
# df2.insert(10, 'height', height)
# df2.insert(11, 'height_lowest', height_lowest)
# df2.insert(12, 'height_highest', height_highest)
# df2[['length', 'length_longest', 'length_shortest', 'width', 'width_smallest', 'width_widest', 'height', 'height_lowest', 'height_highest']]

In [96]:
# df_clearn_size = df[['height', 'height_lowest', 'height_highest']]

In [97]:
# df_clearn_size

### Product Information

In [98]:
df6 = df[['summary']]

In [99]:
df_clearn_Product_Information = df6

In [100]:
df_clearn_Product_Information

summary
0                           坐臥兩用床框, 黑色
1          坐臥兩用床附2抽/2床墊, 白色/husvika 偏硬
2             坐臥兩用床附2床墊, 黑色/husvika 偏硬
3          坐臥兩用床附2抽/2床墊, 白色/malfors 偏硬
4                       坐臥兩用床框附2抽屜, 白色
5                      坐臥兩用床框附2抽屜, 黑棕色
6                       坐臥兩用床框附2抽屜, 白色
7                    坐臥兩用床, vansta 深藍色
8        坐臥兩用床附2抽/2床墊, 白色/malfors 軟硬適中
9       坐臥兩用床附2抽/2床墊, 黑棕色/malfors 軟硬適中
10         坐臥兩用床附2抽/2床墊, 白色/moshult 偏硬
11                       坐臥兩用床框/3抽, 白色
12         坐臥兩用床附2抽/2床墊, 白色/malfors 偏硬
13       坐臥兩用床附2抽/2床墊, 白色/malfors 軟硬適中
14         坐臥兩用床附2抽/2床墊, 白色/husvika 偏硬
15          坐臥兩用床附2床墊, 黑色/malfors 軟硬適中
16             雙人加大床框, 白色, 附lönset床底板條
17          雙人加大床框, 白色, 附lönset床底板條/抽屜
18                   雙人加大床框附抽屜/床頭板, 白色
19               雙人床框, 黑棕色, 附luröy床底板條
20                雙人床框, 松木, 附luröy床底板條
21               雙人床框, 白色, 附lönset床底板條
22       雙人床框, 白色, 附lönset床底板條/4件床底收納盒
23      雙人床框, 黑棕色, 附lönset床底板條/2件床底收納盒
24   雙人加大床框, 染白橡木, 附lönset床底板條/2件床底收納盒
25              雙人加大床框, 白色, 附luröy床底板條
26                   雙人掀床, 黑棕色, 附床板條底座
27            雙人加大床框, 染白橡木, 附luröy床底板條
28             雙人床框, 白色, 附luröy床底板條/抽屜
29        雙人床框, 白色, 附lönset床底板條/抽屜/床頭板
30               雙人床框, 樺木, 附lönset床底板條
31      雙人加大床框, 白色, 附luröy床底板條/4件床底收納盒
32    雙人加大床框, 染白橡木, 附luröy床底板條/2件床底收納盒
33        雙人床框, 黑棕色, 附lönset床底板條/4件收納盒
34                雙人床框, 白色, 附luröy床底板條
35                雙人床框, 白色, 附luröy床底板條
36           雙人加大床框, 白色, 附luröy床底板條/抽屜
37              雙人床框, 黑棕色, 附lönset床底板條
38            雙人加大床框, 黑棕色, 附lönset床底板條
39                        床框, 白色/luröy
40       雙人床框, 黑棕色, 附luröy床底板條/4件床底收納盒
41   雙人加大床框, 染白橡木, 附lönset床底板條/4件床底收納盒
42               雙人床框, 棕色, 附lönset床底板條
43         雙人床框, 白色, 附lönset床底板條/4件收納盒
44               雙人床框, 黑色, 附lönset床底板條
45             小型雙人床框, 白色, 附床板條底座/2件抽屜
46                雙人床框, 松木, 附luröy床底板條
47             雙人加大床框, 黑棕色, 附luröy床底板條
48               雙人床框, 白色, 附lönset床底板條
49                           床框附抽屜, 白色
50         雙人床框, 白色, 附luröy床底板條/抽屜/床頭板
51                雙人床框, 樺木, 附luröy床底板條
52               雙人床框, 白色, 附lönset床底板條
53                              床框, 松木
54      雙人加大床框, 白色, 附luröy床底板條/2件床底收納盒
55    雙人加大床框, 黑棕色, 附lönset床底板條/4件床底收納盒
56         雙人床框, 白色, 附lönset床底板條/2件收納盒
57              雙人床框, 鋁質/藤製, 附床底板條/床頭板
58                雙人加大軟墊式床框, 灰色, 附床底板條
59                           床框附抽屜, 白色
60             雙人加大床框, 黑棕色, 附luröy床底板條
61        雙人床框, 白色, 附luröy床底板條/2件床底收納盒
62                雙人床框, 棕色, 附luröy床底板條
63          雙人床框, 棕色, 附luröy床底板條/4件收納盒
64          雙人床框, 白色, 附luröy床底板條/4件收納盒
65                床框, 白色, 附床底板條/抽屜/床頭板
66               雙人床框, 樺木, 附lönset床底板條
67                雙人床框, 黑色, 附luröy床底板條
68                              床框, 白色
69             雙人加大床框, 白色, 附lönset床底板條
70           小型雙人床框, 白色, 附床板條底座/10件抽屜櫃
71                  雙人軟墊式床框, 灰色, 附床底板條
72              雙人加大床框, 白色, 附luröy床底板條
73            雙人加大床框, 黑棕色, 附lönset床底板條
74              雙人床框, 黑棕色, 附lönset床底板條
75               雙人床框, 白色, 附lönset床底板條
76           雙人加大床框, 染白橡木, 附lönset床底板條
77                雙人床框, 白色, 附luröy床底板條
78                              床框, 白色
79       雙人床框, 黑棕色, 附luröy床底板條/2件床底收納盒
80    雙人加大床框, 黑棕色, 附lönset床底板條/2件床底收納盒
81      雙人床框, 染白橡木, 附luröy床底板條/4件床底收納盒
82        雙人床框, 棕色, 附lönset床底板條/附2件收納盒
83          雙人床框, 白色, 附luröy床底板條/2件收納盒
84               雙人床框, 棕色, 附lönset床底板條
85               雙人床框, 白色, 附lönset床底板條
86               雙人床框, 白色, 附lönset床底板條
87               雙人床框, 鋁質/黑色, 附床頭板/2邊桌
88      雙人加大床框, 白色, 附lönset床底板條/抽屜/床頭板
89             雙人加大床框, 白色, 附lönset床底板條
90     雙人加大床框, 白色, 附lönset床底板條/4件床底收納盒
91     雙人加大床框, 黑棕色, 附luröy床底板條/2件床底收納盒
92     雙人床框, 染白橡木, 附lönset床底板條/2件床底收納盒
93                雙人床框, 樺木, 附luröy床底板條
94                 雙人床框, 鋁質, 附床底板條/2邊桌
95              小型雙人床框,白色, 附床板條底座/4件抽屜
96                雙人軟墊式床框, 黑色, 附床底板條底座
97          雙人床框, 黑棕色, 附luröy床底板條/高床頭板
98              雙人床框, 染白橡木, 附luröy床底板條
99                       床框附抽屜/床頭板, 白色
100       雙人床框, 白色, 附luröy床底板條/4件床底收納盒
101     雙人床框, 染白橡木, 附luröy床底板條/2件床底收納盒
102         雙人

### url

In [101]:
df5 = pd.read_csv('D:/pytel_data/outhet_excel_2/df_funiture_url_remix.csv',encoding='utf8')

In [102]:
df_funiture_url_clearn = df5[['funiture_url']]

In [103]:
df_funiture_url_clearn

funiture_url
0    https://www.ikea.com.tw/dairyfarm/tw/images/49...
1    https://www.ikea.com.tw/dairyfarm/tw/images/54...
2    https://www.ikea.com.tw/dairyfarm/tw/images/49...
3    https://www.ikea.com.tw/dairyfarm/tw/images/54...
4    https://www.ikea.com.tw/dairyfarm/tw/images/54...
5    https://www.ikea.com.tw/dairyfarm/tw/images/54...
6    https://www.ikea.com.tw/dairyfarm/tw/images/54...
7    https://www.ikea.com.tw/dairyfarm/tw/images/35...
8    https://www.ikea.com.tw/dairyfarm/tw/images/54...
9    https://www.ikea.com.tw/dairyfarm/tw/images/54...
10   https://www.ikea.com.tw/dairyfarm/tw/images/54...
11   https://www.ikea.com.tw/dairyfarm/tw/images/36...
12   https://www.ikea.com.tw/dairyfarm/tw/images/54...
13   https://www.ikea.com.tw/dairyfarm/tw/images/54...
14   https://www.ikea.com.tw/dairyfarm/tw/images/54...
15   https://www.ikea.com.tw/dairyfarm/tw/images/49...
16   https://www.ikea.com.tw/dairyfarm/tw/images/49...
17   https://www.ikea.com.tw/dairyfarm/tw/images/37...
18   https://www.ikea.com.tw/dairyfarm/tw/images/38...
19   https://www.ikea.com.tw/dairyfarm/tw/images/37...
20   https://www.ikea.com.tw/dairyfarm/tw/images/37...
21   https://www.ikea.com.tw/dairyfarm/tw/images/37...
22   https://www.ikea.com.tw/dairyfarm/tw/images/38...
23   https://www.ikea.com.tw/dairyfarm/tw/images/37...
24   https://www.ikea.com.tw/dairyfarm/tw/images/38...
25   https://www.ikea.com.tw/dairyfarm/tw/images/37...
26   https://www.ikea.com.tw/dairyfarm/tw/images/49...
27   https://www.ikea.com.tw/dairyfarm/tw/images/37...
28   https://www.ikea.com.tw/dairyfarm/tw/images/37...
29   https://www.ikea.com.tw/dairyfarm/tw/images/38...
30   https://www.ikea.com.tw/dairyfarm/tw/images/37...
31   https://www.ikea.com.tw/dairyfarm/tw/images/38...
32   https://www.ikea.com.tw/dairyfarm/tw/images/38...
33   https://www.ikea.com.tw/dairyfarm/tw/images/38...
34   https://www.ikea.com.tw/dairyfarm/tw/images/38...
35   https://www.ikea.com.tw/dairyfarm/tw/images/37...
36   https://www.ikea.com.tw/dairyfarm/tw/images/37...
37   https://www.ikea.com.tw/dairyfarm/tw/images/37...
38   https://www.ikea.com.tw/dairyfarm/tw/images/37...
39   https://www.ikea.com.tw/dairyfarm/tw/images/37...
40   https://www.ikea.com.tw/dairyfarm/tw/images/37...
41   https://www.ikea.com.tw/dairyfarm/tw/images/38...
42   https://www.ikea.com.tw/dairyfarm/tw/images/38...
43   https://www.ikea.com.tw/dairyfarm/tw/images/37...
44   https://www.ikea.com.tw/dairyfarm/tw/images/83...
45   https://www.ikea.com.tw/dairyfarm/tw/images/46...
46   https://www.ikea.com.tw/dairyfarm/tw/images/49...
47   https://www.ikea.com.tw/dairyfarm/tw/images/38...
48   https://www.ikea.com.tw/dairyfarm/tw/images/49...
49   https://www.ikea.com.tw/dairyfarm/tw/images/37...
50   https://www.ikea.com.tw/dairyfarm/tw/images/38...
51   https://www.ikea.com.tw/dairyfarm/tw/images/37...
52   https://www.ikea.com.tw/dairyfarm/tw/images/37...
53   https://www.ikea.com.tw/dairyfarm/tw/images/37...
54   https://www.ikea.com.tw/dairyfarm/tw/images/38...
55   https://www.ikea.com.tw/dairyfarm/tw/images/37...
56   https://www.ikea.com.tw/dairyfarm/tw/images/37...
57   https://www.ikea.com.tw/dairyfarm/tw/images/60...
58   https://www.ikea.com.tw/dairyfarm/tw/images/89...
59   https://www.ikea.com.tw/dairyfarm/tw/images/37...
60   https://www.ikea.com.tw/dairyfarm/tw/images/37...
61   https://www.ikea.com.tw/dairyfarm/tw/images/38...
62   https://www.ikea.com.tw/dairyfarm/tw/images/38...
63   https://www.ikea.com.tw/dairyfarm/tw/images/38...
64   https://www.ikea.com.tw/dairyfarm/tw/images/37...
65   https://www.ikea.com.tw/dairyfarm/tw/images/49...
66   https://www.ikea.com.tw/dairyfarm/tw/images/29...
67   https://www.ikea.com.tw/dairyfarm/tw/images/83...
68   https://www.ikea.com.tw/dairyfarm/tw/images/37...
69   https://www.ikea.com.tw/dairyfarm/tw/images/37...
70   https://www.ikea.com.tw/dairyfarm/tw/images/46...
71   https://www.ikea.com.tw/dairyfarm/tw/images/89...
72   https://www.ikea.com.t

### remix

In [104]:
#pd.set_option('display.max_columns', None)

In [105]:
df_clearn_all = pd.concat([df_clearn_Product_number_n['Product_number_clearn'], 
                           df['url'], df_funiture_url_clearn, 
                           df_clearn_price_n['price_clearn'], 
                           df['title'], 
                           df_clearn_Product_Information, 
                           df['type'], 
                           df_clearn_size_remix, 
                           df_clearn_color_remix,
                           df_new_color_c,
                           df['style'], 
                           df['style_url']], axis=1)

In [106]:
df_clearn_all

Product_number_clearn                                                url  \
0              004.243.63  https://www.ikea.com.tw/zh/products/beds/flexi...   
1              091.838.68  https://www.ikea.com.tw/zh/products/beds/flexi...   
2              092.792.91  https://www.ikea.com.tw/zh/products/beds/flexi...   
3              391.987.88  https://www.ikea.com.tw/zh/products/beds/flexi...   
4              403.201.32  https://www.ikea.com.tw/zh/products/beds/flexi...   
5              503.201.36  https://www.ikea.com.tw/zh/products/beds/flexi...   
6              503.544.85  https://www.ikea.com.tw/zh/products/beds/flexi...   
7              504.544.42  https://www.ikea.com.tw/zh/products/beds/flexi...   
8              591.987.87  https://www.ikea.com.tw/zh/products/beds/flexi...   
9              691.299.39  https://www.ikea.com.tw/zh/products/beds/flexi...   
10             691.987.58  https://www.ikea.com.tw/zh/products/beds/flexi...   
11             703.493.27  https://www.ikea.com.tw/zh/products/beds/flexi...   
12             891.298.77  https://www.ikea.com.tw/zh/products/beds/flexi...   
13             891.299.43  https://www.ikea.com.tw/zh/products/beds/flexi...   
14             891.987.57  https://www.ikea.com.tw/zh/products/beds/flexi...   
15             892.792.92  https://www.ikea.com.tw/zh/products/beds/flexi...   
16             090.191.42  https://www.ikea.com.tw/zh/products/beds/bed-f...   
17             091.981.53  https://www.ikea.com.tw/zh/products/beds/bed-f...   
18             091.981.67  https://www.ikea.com.tw/zh/products/beds/bed-f...   
19             091.982.33  https://www.ikea.com.tw/zh/products/beds/bed-f...   
20             091.985.15  https://www.ikea.com.tw/zh/products/beds/bed-f...   
21             091.986.38  https://www.ikea.com.tw/zh/products/beds/bed-f...   
22             091.998.93  https://www.ikea.com.tw/zh/products/beds/bed-f...   
23             092.008.77  https://www.ikea.com.tw/zh/products/beds/bed-f...   
24             092.010.18  https://www.ikea.com.tw/zh/products/beds/bed-f...   
25             092.772.87  https://www.ikea.com.tw/zh/products/beds/bed-f...   
26             104.048.02  https://www.ikea.com.tw/zh/products/beds/bed-f...   
27             190.273.92  https://www.ikea.com.tw/zh/products/beds/bed-f...   
28             191.981.43  https://www.ikea.com.tw/zh/products/beds/bed-f...   
29             191.981.62  https://www.ikea.com.tw/zh/products/beds/bed-f...   
30             191.982.18  https://www.ikea.com.tw/zh/products/beds/bed-f...   
31             191.997.79  https://www.ikea.com.tw/zh/products/beds/bed-f...   
32             192.009.71  https://www.ikea.com.tw/zh/products/beds/bed-f...   
33             192.411.65  https://www.ikea.com.tw/zh/products/beds/bed-f...   
34             192.412.88  https://www.ikea.com.tw/zh/products/beds/bed-f...   
35             192.772.82  https://www.ikea.com.tw/zh/products/beds/bed-f...   
36             291.981.52  https://www.ikea.com.tw/zh/products/beds/bed-f...   
37             291.982.65  https://www.ikea.com.tw/zh/products/beds/bed-f...   
38             291.983.93  https://www.ikea.com.tw/zh/products/beds/bed-f...   
39             291.986.37  https://www.ikea.com.tw/zh/products/beds/bed-f...   
40             292.006.21  https://www.ikea.com.tw/zh/products/beds/bed-f...   
41             292.010.17  https://www.ikea.com.tw/zh/products/beds/bed-f...   
42             292.410.75  https://www.ikea.com.tw/zh/products/beds/bed-f...   
43             292.413.44  https://www.ikea.com.tw/zh/products/beds/bed-f...   
44             292.689.13  https://www.ikea.com.tw/zh/products/beds/bed-f...   
45             293.030.06  https://www.ikea.com.tw/zh/products/beds/bed-f...   
46             293.037.42  https://www.ikea.com.tw/zh/products/beds/bed-f...   
47             390.094.53  https://www.ikea.com.tw/zh/products/beds/bed-f...   
48             390.191.88  https://www.ikea.com.tw/zh/products/beds/bed-f...   
49  

In [107]:
df_clearn_all.columns = ['Product_number', 
                         'url', 
                         'funiture_url', 
                         'price', 
                         'title', 
                         'summary', 
                         'category', 
                         'length', 
                         'length_longest', 
                         'length_shortest', 
                         'width', 'width_smallest', 
                         'width_widest', 
                         'height', 
                         'height_lowest', 
                         'height_highest', 
                         'color_1', 
                         'color_2', 
                         'color_3',
                         'new_color_1',
                         'new_color_2',
                         'new_color_3',
                         'style', 
                         'style_url']

In [108]:
df_clearn_all

Product_number                                                url  \
0       004.243.63  https://www.ikea.com.tw/zh/products/beds/flexi...   
1       091.838.68  https://www.ikea.com.tw/zh/products/beds/flexi...   
2       092.792.91  https://www.ikea.com.tw/zh/products/beds/flexi...   
3       391.987.88  https://www.ikea.com.tw/zh/products/beds/flexi...   
4       403.201.32  https://www.ikea.com.tw/zh/products/beds/flexi...   
5       503.201.36  https://www.ikea.com.tw/zh/products/beds/flexi...   
6       503.544.85  https://www.ikea.com.tw/zh/products/beds/flexi...   
7       504.544.42  https://www.ikea.com.tw/zh/products/beds/flexi...   
8       591.987.87  https://www.ikea.com.tw/zh/products/beds/flexi...   
9       691.299.39  https://www.ikea.com.tw/zh/products/beds/flexi...   
10      691.987.58  https://www.ikea.com.tw/zh/products/beds/flexi...   
11      703.493.27  https://www.ikea.com.tw/zh/products/beds/flexi...   
12      891.298.77  https://www.ikea.com.tw/zh/products/beds/flexi...   
13      891.299.43  https://www.ikea.com.tw/zh/products/beds/flexi...   
14      891.987.57  https://www.ikea.com.tw/zh/products/beds/flexi...   
15      892.792.92  https://www.ikea.com.tw/zh/products/beds/flexi...   
16      090.191.42  https://www.ikea.com.tw/zh/products/beds/bed-f...   
17      091.981.53  https://www.ikea.com.tw/zh/products/beds/bed-f...   
18      091.981.67  https://www.ikea.com.tw/zh/products/beds/bed-f...   
19      091.982.33  https://www.ikea.com.tw/zh/products/beds/bed-f...   
20      091.985.15  https://www.ikea.com.tw/zh/products/beds/bed-f...   
21      091.986.38  https://www.ikea.com.tw/zh/products/beds/bed-f...   
22      091.998.93  https://www.ikea.com.tw/zh/products/beds/bed-f...   
23      092.008.77  https://www.ikea.com.tw/zh/products/beds/bed-f...   
24      092.010.18  https://www.ikea.com.tw/zh/products/beds/bed-f...   
25      092.772.87  https://www.ikea.com.tw/zh/products/beds/bed-f...   
26      104.048.02  https://www.ikea.com.tw/zh/products/beds/bed-f...   
27      190.273.92  https://www.ikea.com.tw/zh/products/beds/bed-f...   
28      191.981.43  https://www.ikea.com.tw/zh/products/beds/bed-f...   
29      191.981.62  https://www.ikea.com.tw/zh/products/beds/bed-f...   
30      191.982.18  https://www.ikea.com.tw/zh/products/beds/bed-f...   
31      191.997.79  https://www.ikea.com.tw/zh/products/beds/bed-f...   
32      192.009.71  https://www.ikea.com.tw/zh/products/beds/bed-f...   
33      192.411.65  https://www.ikea.com.tw/zh/products/beds/bed-f...   
34      192.412.88  https://www.ikea.com.tw/zh/products/beds/bed-f...   
35      192.772.82  https://www.ikea.com.tw/zh/products/beds/bed-f...   
36      291.981.52  https://www.ikea.com.tw/zh/products/beds/bed-f...   
37      291.982.65  https://www.ikea.com.tw/zh/products/beds/bed-f...   
38      291.983.93  https://www.ikea.com.tw/zh/products/beds/bed-f...   
39      291.986.37  https://www.ikea.com.tw/zh/products/beds/bed-f...   
40      292.006.21  https://www.ikea.com.tw/zh/products/beds/bed-f...   
41      292.010.17  https://www.ikea.com.tw/zh/products/beds/bed-f...   
42      292.410.75  https://www.ikea.com.tw/zh/products/beds/bed-f...   
43      292.413.44  https://www.ikea.com.tw/zh/products/beds/bed-f...   
44      292.689.13  https://www.ikea.com.tw/zh/products/beds/bed-f...   
45      293.030.06  https://www.ikea.com.tw/zh/products/beds/bed-f...   
46      293.037.42  https://www.ikea.com.tw/zh/products/beds/bed-f...   
47      390.094.53  https://www.ikea.com.tw/zh/products/beds/bed-f...   
48      390.191.88  https://www.ikea.com.tw/zh/products/beds/bed-f...   
49      391.981.42  https://www.ikea.com.tw/zh/products/beds/bed-f...   
50      391.981.61  https://www.ikea.com.tw/zh/products/beds/bed-f...   
51      391.982.17  https://www.ikea.com.tw/zh/products/beds/bed-f...   
52      391.983.97  https://www.ikea.com.tw/zh/products/beds/bed-f...   
53      391.985.14  https://www.ikea.com.tw/zh/products/beds/b

In [109]:
df_clearn_all.to_csv(r'D:/pytel_data/outhet_excel_2/ikeamaster_ver7_cl_f6.csv', encoding='utf-8')

In [110]:
# df_clearn_all_t.to_csv(r'D:/pytel_data/outhet_excel_2/ikeamaster_ver7_c3_t.csv', encoding='utf-8')